# 1. 불러오기

In [2]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## 1.1 라이브러리 불러오기

In [3]:
import sys
sys.path.append('src')
import enex_analysis as enex
import scipy.stats as st
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import dartwork_mpl as dm
import seaborn as sns
import warnings
warnings.filterwarnings("ignore")
import matplotlib.colors as mcolors
from matplotlib.cm import get_cmap
from matplotlib import cm
from matplotlib.patches import Patch
from mpl_toolkits.axes_grid1 import make_axes_locatable
import math

dm.use_style()

Load colors...
Load colormaps...


## 1.2 파일 불러오기

In [4]:
# small office 데이터 파일 불러오기
file_path = 'data/'
small_office_df = pd.read_csv(file_path + 'small_office_hour.csv')
# small_office_df = pd.read_csv(file_path + 'dual_setpoint_smalloffice.csv')

# 데이터프레임의 컬럼 이름 프린트
print(small_office_df.columns)

Index(['Date/Time',
       'Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)',
       'ATTIC:Zone Air Temperature [C](TimeStep)',
       'CORE_ZN:Zone Air Temperature [C](TimeStep)',
       'PERIMETER_ZN_1:Zone Air Temperature [C](TimeStep)',
       'PERIMETER_ZN_2:Zone Air Temperature [C](TimeStep)',
       'PERIMETER_ZN_3:Zone Air Temperature [C](TimeStep)',
       'PERIMETER_ZN_4:Zone Air Temperature [C](TimeStep)',
       'ATTIC IDEAL LOADS AIR SYSTEM:Zone Ideal Loads Zone Total Heating Energy [J](TimeStep)',
       'ATTIC IDEAL LOADS AIR SYSTEM:Zone Ideal Loads Zone Total Cooling Energy [J](TimeStep)',
       'CORE_ZN IDEAL LOADS AIR SYSTEM:Zone Ideal Loads Zone Total Heating Energy [J](TimeStep)',
       'CORE_ZN IDEAL LOADS AIR SYSTEM:Zone Ideal Loads Zone Total Cooling Energy [J](TimeStep)',
       'PERIMETER_ZN_1 IDEAL LOADS AIR SYSTEM:Zone Ideal Loads Zone Total Heating Energy [J](TimeStep)',
       'PERIMETER_ZN_1 IDEAL LOADS AIR SYSTEM:Zone Ideal Loads Zone To

## 1.3 주말 부하 = 0 으로 설정 + 10-3월은 난방만, 4-9월은 냉방만 발생

In [5]:
# 1. Date/Time 열 공백 정리
weekday_df = small_office_df.copy()
weekday_df['Date/Time_clean'] = weekday_df['Date/Time'].str.strip().str.replace(r'\s+', ' ', regex=True)

# 2. 시간 인덱스 기반으로 '요일' 계산 (1월 1일 = 일요일)
weekday_df['Relative_Day_Index'] = weekday_df.index // 24
weekday_df['Day'] = (6 + weekday_df['Relative_Day_Index']) % 7 

# 3. 평일 데이터만 필터링 (Weekday 0~4 → 월~금)
weekday_df.loc[weekday_df['Day'].isin([5, 6]), 'DistrictCooling:Facility [J](TimeStep)'] = 0
weekday_df.loc[weekday_df['Day'].isin([5, 6]), 'DistrictHeatingWater:Facility [J](TimeStep) '] = 0
# weekday_df.loc[weekday_df['Day'].isin([5, 6]), 'DistrictCooling:Facility [J](TimeStep) '] = 0
# weekday_df.loc[weekday_df['Day'].isin([5, 6]), 'DistrictHeating:Facility [J](TimeStep)'] = 0

# 4. 10-3월은 난방만, 4-9월은 냉방만 발생하도록 설정
# 월 정보 추출
weekday_df['Month'] = weekday_df['Date/Time_clean'].str.slice(0, 2).astype(int)
# 난방월에는 냉방 부하를 0으로 설정
weekday_df.loc[weekday_df['Month'].isin([1, 2, 3, 10, 11, 12]), 'DistrictCooling:Facility [J](TimeStep)'] = 0
# 냉방월에는 난방 부하를 0으로 설정
weekday_df.loc[weekday_df['Month'].isin([4, 5, 6, 7, 8, 9]), 'DistrictHeatingWater:Facility [J](TimeStep) '] = 0

# 4. 필요시 인덱스 초기화
weekday_df.reset_index(drop=True, inplace=True)

## 1.4 환경온도, 실내온도, 부하 리스트 생성

In [ ]:
# 변수(환경온도, 실내온도, 부하) 리스트 생성
date_list = weekday_df['Date/Time_clean'] # 날짜
Toa_list = weekday_df['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)'] # 환경온도
Tia_list = weekday_df['CORE_ZN:Zone Air Temperature [C](TimeStep)'] # 실내온도
cooling_load_list = weekday_df['DistrictCooling:Facility [J](TimeStep)'] / 3600 # 냉방부하, J -> W
heating_load_list = weekday_df['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600 # 난방부하, J -> W
ATTIC_ZT = weekday_df['ATTIC:Zone Air Temperature [C](TimeStep)'] # 옥상 온도
CORE_ZT = weekday_df['CORE_ZN:Zone Air Temperature [C](TimeStep)'] # 실내 온도
PERIMETER_Z1T = weekday_df['PERIMETER_ZN_1:Zone Air Temperature [C](TimeStep)'] # 주변 온도
PERIMETER_Z2T = weekday_df['PERIMETER_ZN_2:Zone Air Temperature [C](TimeStep)'] # 주변 온도
PERIMETER_Z3T = weekday_df['PERIMETER_ZN_3:Zone Air Temperature [C](TimeStep)'] # 주변 온도
PERIMETER_Z4T = weekday_df['PERIMETER_ZN_4:Zone Air Temperature [C](TimeStep)'] # 주변 온도
Date = weekday_df['Date/Time'] # 날짜

Zone_temp_list = [CORE_ZT, PERIMETER_Z1T, PERIMETER_Z2T, PERIMETER_Z3T, PERIMETER_Z4T]

# 리스트 길이 확인
len(date_list), len(Toa_list), len(Tia_list), len(cooling_load_list), len(heating_load_list), len(Date)

(8760, 8760, 8760, 8760, 8760, 8760)

## 1.5 COP, 엑서지 효율 리스트 생성

In [7]:
ASHP_cooling_exergy_effi = []
ASHP_heating_exergy_effi = []
ASHP_cooling_COP = []
ASHP_heating_COP = []
dV_int_cooling_list = []
dV_ext_cooling_list = []
dV_int_heating_list = []
dV_ext_heating_list = []

for Toa, cooling_load, heating_load in zip(Toa_list, cooling_load_list, heating_load_list):
    # 냉방 엑서지 효율 계산
    if cooling_load > 0:
        ASHP_cooling = enex.AirSourceHeatPump_cooling()
        ASHP_cooling.T0 = Toa
        ASHP_cooling.T_a_room = 22
        ASHP_cooling.Q_r_int = cooling_load
        ASHP_cooling.Q_r_max = max(cooling_load_list)
        ASHP_cooling.system_update()
        if ASHP_cooling.X_eff < 0:
            ASHP_cooling_exergy_effi.append(None)
            ASHP_cooling_COP.append(None)
        else:          
            ASHP_cooling_exergy_effi.append(ASHP_cooling.X_eff)
            ASHP_cooling_COP.append(ASHP_cooling.COP_sys)
            dV_int_cooling_list.append(ASHP_cooling.dV_int)
            dV_ext_cooling_list.append(ASHP_cooling.dV_ext)
    else:
        ASHP_cooling_exergy_effi.append(None)
        ASHP_cooling_COP.append(None)

    # 난방 엑서지 효율 계산
    if heating_load > 0:
        ASHP_heating = enex.AirSourceHeatPump_heating()
        ASHP_heating.T0 = Toa
        ASHP_heating.T_a_room = 22
        ASHP_heating.Q_r_int = heating_load
        ASHP_heating.Q_r_max = max(heating_load_list)
        ASHP_heating.system_update() 
        if ASHP_heating.X_eff < 0:
            ASHP_heating_exergy_effi.append(None)
            ASHP_heating_COP.append(None)
        else:
            ASHP_heating_exergy_effi.append(ASHP_heating.X_eff)
            ASHP_heating_COP.append(ASHP_heating.COP_sys)
            dV_int_heating_list.append(ASHP_heating.dV_int)
            dV_ext_heating_list.append(ASHP_heating.dV_ext)
    else:
        ASHP_heating_exergy_effi.append(None)
        ASHP_heating_COP.append(None)

# COP None 값일 때 해당하는 COP를 제거한 필터링된 리스트
ASHP_cooling_COP_filtered = [cop for cop in ASHP_cooling_COP if cop is not None]
ASHP_heating_COP_filtered = [cop for cop in ASHP_heating_COP if cop is not None]
ASHP_cooling_exergy_effi_filtered = [eff for eff in ASHP_cooling_exergy_effi if eff is not None]
ASHP_heating_exergy_effi_filtered = [eff for eff in ASHP_heating_exergy_effi if eff is not None]

# 엑서지효율 None 값일 때 해당하는 온도, 부하를 제거한 필터링된 리스트
Date_cooling_list_filtered = [date for date, eff in zip(date_list, ASHP_cooling_exergy_effi) if eff is not None]
Date_heating_list_filtered = [date for date, eff in zip(date_list, ASHP_heating_exergy_effi) if eff is not None]
Tia_cooling_list_filtered = [Tia for Tia, eff in zip(Tia_list, ASHP_cooling_exergy_effi) if eff is not None]
Tia_heating_list_filtered = [Tia for Tia, eff in zip(Tia_list, ASHP_heating_exergy_effi) if eff is not None]
Toa_cooling_list_filtered = [Toa for Toa, eff in zip(Toa_list, ASHP_cooling_exergy_effi) if eff is not None]
Toa_heating_list_filtered = [Toa for Toa, eff in zip(Toa_list, ASHP_heating_exergy_effi) if eff is not None]
cooling_load_list_filtered = [load for load, eff in zip(cooling_load_list, ASHP_cooling_exergy_effi) if eff is not None]
heating_load_list_filtered = [load for load, eff in zip(heating_load_list, ASHP_heating_exergy_effi) if eff is not None]

len(ASHP_cooling_COP_filtered), len(ASHP_heating_COP_filtered), len(Date_cooling_list_filtered), len(Date_heating_list_filtered), len(Tia_cooling_list_filtered), len(Tia_heating_list_filtered), len(Toa_cooling_list_filtered), len(Toa_heating_list_filtered), len(cooling_load_list_filtered), len(heating_load_list_filtered)

(1693, 1701, 1693, 1701, 1693, 1701, 1693, 1701, 1693, 1701)

In [8]:
round(max(cooling_load_list), 0), round(max(heating_load_list), 0)

(23747.0, 27408.0)

# Exergy demand

## Exergy demand 리스트 생성

In [5]:
# 카르노 팩터 환경온도 리스트 기반으로 계산
carnot_factor = 1 - (cu.C2K(np.array(Toa_list)) / cu.C2K(np.array(Tia_list)))

# Exergy demand
exergy_cooling_load_list = - cooling_load_list / 511 * carnot_factor
exergy_heating_load_list = heating_load_list / 511 * carnot_factor

In [45]:
ASHP_cooling_exergy_effi = []
ASHP_heating_exergy_effi = []

for Toa, Tia, cooling_load, heating_load in zip(Toa_list, Tia_list, cooling_load_list, heating_load_list):
    # 냉방 엑서지 효율 계산
    if cooling_load > 0:
        ASHP_cooling = AirSourceHeatPump_cooling()
        ASHP_cooling.T_0 = cu.C2K(Toa)
        ASHP_cooling.T_a_int_in = cu.C2K(Tia)
        ASHP_cooling.Q_r_int = cooling_load
        ASHP_cooling.COP_model.max_cooling_load = max(cooling_load_list)
        ASHP_cooling.system_update()
        cooling_exergy_efficiency = ASHP_cooling.Xout_int / (ASHP_cooling.E_fan_int + ASHP_cooling.E_cmp + ASHP_cooling.E_fan_ext)
        if ASHP_cooling.Xout_int < 0:
            ASHP_cooling_exergy_effi.append(cooling_exergy_efficiency)
        else:
            ASHP_cooling_exergy_effi.append(cooling_exergy_efficiency)
    else:
        ASHP_cooling_exergy_effi.append(None)

    # 난방 엑서지 효율 계산
    if heating_load > 0:
        ASHP_heating = AirSourceHeatPump_heating()
        ASHP_heating.T_0 = cu.C2K(Toa)
        ASHP_heating.T_a_int_in = cu.C2K(Tia)
        ASHP_heating.Q_r_int = heating_load
        ASHP_heating.COP_model.max_heating_load = max(heating_load_list)
        ASHP_heating.system_update()
        heating_exergy_efficiency = ASHP_heating.Xout_int / (ASHP_heating.E_fan_int + ASHP_heating.E_cmp + ASHP_heating.E_fan_ext)
        if ASHP_heating.Xout_int < 0:
            ASHP_heating_exergy_effi.append(heating_exergy_efficiency)
        else:
            ASHP_heating_exergy_effi.append(heating_exergy_efficiency)
    else:
        ASHP_heating_exergy_effi.append(None)

# 엑서지효율 None 제거
ASHP_cooling_exergy_effi_filtered = [x for x in ASHP_cooling_exergy_effi if x is not None]
ASHP_heating_exergy_effi_filtered = [x for x in ASHP_heating_exergy_effi if x is not None]

# 엑서지효율 None 값일 때 해당하는 온도, 부하를 제거한 필터링된 리스트
Date_cooling_list_filtered = [date for date, eff in zip(date_list, ASHP_cooling_exergy_effi) if eff is not None]
Date_heating_list_filtered = [date for date, eff in zip(date_list, ASHP_heating_exergy_effi) if eff is not None]
Tia_cooling_list_filtered = [Tia for Tia, eff in zip(Tia_list, ASHP_cooling_exergy_effi) if eff is not None]
Tia_heating_list_filtered = [Tia for Tia, eff in zip(Tia_list, ASHP_heating_exergy_effi) if eff is not None]
Toa_cooling_list_filtered = [Toa for Toa, eff in zip(Toa_list, ASHP_cooling_exergy_effi) if eff is not None]
Toa_heating_list_filtered = [Toa for Toa, eff in zip(Toa_list, ASHP_heating_exergy_effi) if eff is not None]
cooling_load_list_filtered = [load for load, eff in zip(cooling_load_list, ASHP_cooling_exergy_effi) if eff is not None]
heating_load_list_filtered = [load for load, eff in zip(heating_load_list, ASHP_heating_exergy_effi) if eff is not None]
exergy_cooling_load_list_filtered = [load for load, eff in zip(exergy_cooling_load_list, ASHP_cooling_exergy_effi) if eff is not None]
exergy_heating_load_list_filtered = [load for load, eff in zip(exergy_heating_load_list, ASHP_heating_exergy_effi) if eff is not None]

len(Date_cooling_list_filtered), len(Date_heating_list_filtered), len(Tia_cooling_list_filtered), len(Tia_heating_list_filtered), len(Toa_cooling_list_filtered), len(Toa_heating_list_filtered), len(cooling_load_list_filtered), len(heating_load_list_filtered)

(2602, 1976, 2602, 1976, 2602, 1976, 2602, 1976)

## Exergy demand 관련 그래프

Thermal load와 Exergy demand 같이 그리기

In [55]:
ASHP_cooling_none_to_zero_exergy_effi = []
ASHP_heating_none_to_zero_exergy_effi = []

for Toa, Tia, cooling_load, heating_load in zip(Toa_list, Tia_list, cooling_load_list, heating_load_list):
    # 냉방 엑서지 효율 계산
    if cooling_load > 0:
        ASHP_cooling = AirSourceHeatPump_cooling()
        ASHP_cooling.T_0 = cu.C2K(Toa)
        ASHP_cooling.T_a_int_in = cu.C2K(Tia)
        ASHP_cooling.Q_r_int = cooling_load
        ASHP_cooling.COP_model.max_cooling_load = max(cooling_load_list)
        ASHP_cooling.system_update()
        cooling_exergy_efficiency = ASHP_cooling.Xout_int / (ASHP_cooling.E_fan_int + ASHP_cooling.E_cmp + ASHP_cooling.E_fan_ext)
        if ASHP_cooling.Xout_int < 0:
            ASHP_cooling_none_to_zero_exergy_effi.append(cooling_exergy_efficiency)
        else:
            ASHP_cooling_none_to_zero_exergy_effi.append(cooling_exergy_efficiency)
    else:
        ASHP_cooling_none_to_zero_exergy_effi.append(0)

    # 난방 엑서지 효율 계산
    if heating_load > 0:
        ASHP_heating = AirSourceHeatPump_heating()
        ASHP_heating.T_0 = cu.C2K(Toa)
        ASHP_heating.T_a_int_in = cu.C2K(Tia)
        ASHP_heating.Q_r_int = heating_load
        ASHP_heating.COP_model.max_heating_load = max(heating_load_list)
        ASHP_heating.system_update()
        heating_exergy_efficiency = ASHP_heating.Xout_int / (ASHP_heating.E_fan_int + ASHP_heating.E_cmp + ASHP_heating.E_fan_ext)
        if ASHP_heating.Xout_int < 0:
            ASHP_heating_none_to_zero_exergy_effi.append(heating_exergy_efficiency)
        else:
            ASHP_heating_none_to_zero_exergy_effi.append(heating_exergy_efficiency)
    else:
        ASHP_heating_none_to_zero_exergy_effi.append(0)

In [67]:
# 쿨링 조건 인덱스
cooling_efficiency_indices = {
    i for i in range(len(ASHP_cooling_none_to_zero_exergy_effi))
    if ASHP_cooling_none_to_zero_exergy_effi[i] < 0
}
cooling_load_indices = {
    i for i in range(len(exergy_cooling_load_list))
    if exergy_cooling_load_list[i] < 0
}

# 히팅 조건 인덱스
heating_efficiency_indices = {
    i for i in range(len(ASHP_heating_none_to_zero_exergy_effi))
    if ASHP_heating_none_to_zero_exergy_effi[i] < 0
}
heating_load_indices = {
    i for i in range(len(exergy_heating_load_list))
    if exergy_heating_load_list[i] < 0
}

# 쿨링 비교
if cooling_efficiency_indices == cooling_load_indices and len(cooling_efficiency_indices) > 0:
    print("쿨링에서는 모두 동일합니다.")
else:
    only_in_eff = sorted(cooling_efficiency_indices - cooling_load_indices)
    only_in_load = sorted(cooling_load_indices - cooling_efficiency_indices)
    print("쿨링 - 서로 다른 인덱스 존재:")
    if only_in_eff:
        print(f"엑서지 효율 조건만 만족하는 인덱스: {only_in_eff}")
    if only_in_load:
        print(f"엑서지 부하 조건만 만족하는 인덱스: {only_in_load}")

# 히팅 비교
if heating_efficiency_indices == heating_load_indices and len(heating_efficiency_indices) > 0:
    print("히팅에서도 모두 동일합니다.")
else:
    only_in_eff = sorted(heating_efficiency_indices - heating_load_indices)
    only_in_load = sorted(heating_load_indices - heating_efficiency_indices)
    print("히팅 - 서로 다른 인덱스 존재:")
    if only_in_eff:
        print(f"엑서지 효율 조건만 만족하는 인덱스: {only_in_eff}")
    if only_in_load:
        print(f"엑서지 부하 조건만 만족하는 인덱스: {only_in_load}")


쿨링 - 서로 다른 인덱스 존재:
엑서지 부하 조건만 만족하는 인덱스: [877, 878, 879, 1598, 1599, 1600, 1907, 1908, 1909, 1910, 1911, 1912, 1956, 1957, 1958, 1959, 1960, 1961, 2102, 2243, 2244, 2245, 2246, 2247, 2269, 2270, 2271, 2461, 2462, 2463, 2464, 2465, 2466, 2482, 2483, 2484, 2485, 2486, 2487, 2558, 2559, 2578, 2579, 2586, 2587, 2588, 2602, 2603, 2604, 2605, 2607, 2608, 2609, 2610, 2611, 2628, 2629, 2630, 2651, 2652, 2653, 2654, 2655, 2656, 2657, 2658, 2720, 2721, 2722, 2731, 2732, 2741, 2742, 2743, 2744, 2745, 2746, 2747, 2748, 2749, 2750, 2751, 2752, 2753, 2754, 2755, 2756, 2767, 2768, 2769, 2770, 2771, 2772, 2773, 2774, 2775, 2776, 2777, 2778, 2779, 2780, 2819, 2820, 2821, 2822, 2823, 2824, 2825, 2890, 2891, 2892, 2893, 2895, 2896, 2897, 2898, 2899, 2965, 2966, 2967, 2968, 2969, 2988, 2989, 2990, 2991, 2992, 3057, 3058, 3067, 3068, 3081, 3082, 3090, 3091, 3092, 3103, 3104, 3105, 3106, 3107, 3108, 3109, 3110, 3111, 3112, 3113, 3114, 3115, 3129, 3130, 3131, 3132, 3133, 3134, 3135, 3136, 3137, 3138, 3139, 31

In [59]:
# Set up the subplots
fig, ax = plt.subplots(3, 1, figsize=(dm.cm2in(14), dm.cm2in(12)))
plt.subplots_adjust(left=0.1, right=0.95, top=0.95, bottom=0.1, hspace=0.3)

# Fontsize
label_fontsize = dm.fs(0)
tick_fontsize = dm.fs(-0.5)
legend_fontsize = dm.fs(-1.0)
subtitle_fontsize = dm.fs(-1.5)

# Common settings
label_pad = 4
line_width = 0.8

# Colors
color_temp = 'dm.green4'
color_cooling = 'dm.blue6'
color_heating = 'dm.red6'

# Plot environmental temperature
ax[0].plot(heating_load_list / 511, color=color_heating, label='Heating hourly load [MJ]', linewidth=line_width, alpha=0.5)
ax[0].plot(cooling_load_list / 511, color=color_cooling, label='Cooling hourly load [MJ]', linewidth=line_width, alpha=0.5)
# ax[0].set_xlabel('Hour of year [h]', fontsize=label_fontsize, labelpad=label_pad)
ax[0].set_ylabel('Thermal demand [W/m²]', fontsize=label_fontsize, labelpad=label_pad)
ax[0].tick_params(axis='both', which='major', labelsize=tick_fontsize)
ax[0].set_xticks(np.linspace(0, 8760, 7))
ax[0].set_yticks(np.arange(0, 61, 10))
ax[0].grid(True, linestyle='--', alpha=0.6)
ax[0].text(0.01, 0.97, '(a)', transform=ax[0].transAxes, fontsize=subtitle_fontsize, fontweight='bold', va='top', ha='left')
ax[0].legend(
    labels=['Heating demand', 'Cooling demand'],
    loc='upper right', ncol=2, frameon=False,
    fontsize=legend_fontsize, fancybox=False,
    columnspacing=1.00, labelspacing=0.8,
    bbox_to_anchor=(0.95, 0.995),
    handlelength=1.8
)

# Plot loads
ax[1].plot(exergy_heating_load_list, color=color_heating, label='Heating hourly load [MJ]', linewidth=line_width, alpha=0.5)
ax[1].plot(exergy_cooling_load_list, color=color_cooling, label='Cooling hourly load [MJ]', linewidth=line_width, alpha=0.5)
# ax[1].set_xlabel('Hour of year [h]', fontsize=label_fontsize, labelpad=label_pad)
ax[1].set_ylabel('Exergy demand [W/m²]', fontsize=label_fontsize, labelpad=label_pad)
ax[1].tick_params(axis='both', which='major', labelsize=tick_fontsize)
ax[1].set_xticks(np.linspace(0, 8760, 7))
ax[1].set_yticks(np.arange(-1, 6, 1))
ax[1].grid(True, linestyle='--', alpha=0.6)
ax[1].text(0.01, 0.97, '(b)', transform=ax[1].transAxes, fontsize=subtitle_fontsize, fontweight='bold', va='top', ha='left')
ax[1].legend(
    labels=['Heating demand', 'Cooling demand'],
    loc='upper right', ncol=2, frameon=False,
    fontsize=legend_fontsize, fancybox=False,
    columnspacing=1.00, labelspacing=0.8,
    bbox_to_anchor=(0.95, 0.995),
    handlelength=1.8
)

# Plot exergy efficiency
ax[2].plot([eff * 100 for eff in ASHP_heating_none_to_zero_exergy_effi], color=color_heating, label='Heating exergy efficiency [%]', linewidth=line_width, alpha=0.5)
ax[2].plot([eff * 100 for eff in ASHP_cooling_none_to_zero_exergy_effi], color=color_cooling, label='Cooling exergy efficiency [%]', linewidth=line_width, alpha=0.5)
ax[2].set_xlabel('Hour of year [h]', fontsize=label_fontsize, labelpad=label_pad)
ax[2].set_ylabel('Exergy efficiency [%]', fontsize=label_fontsize, labelpad=label_pad)
ax[2].tick_params(axis='both', which='major', labelsize=tick_fontsize)
ax[2].set_xticks(np.linspace(0, 8760, 7))
ax[2].set_ylim(-5, 51)
ax[2].set_yticks(np.arange(0, 51, 10))
ax[2].grid(True, linestyle='--', alpha=0.6)
ax[2].text(0.01, 0.97, '(c)', transform=ax[2].transAxes, fontsize=subtitle_fontsize, fontweight='bold', va='top', ha='left')
ax[2].legend(
    labels=['Heating exergy efficiency', 'Cooling exergy efficiency'],
    loc='upper right', ncol=2, frameon=False,
    fontsize=legend_fontsize, fancybox=False,
    columnspacing=1.00, labelspacing=0.8,
    bbox_to_anchor=(0.95, 0.995),
    handlelength=1.8
)

# Save and show the figure
plt.savefig('figure/thermal_load_and_exergy_load.png', dpi=600)
dm.util.save_and_show(fig)


In [147]:
# coolwarm 컬러맵의 왼쪽 절반만 사용
coolwarm_left = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_left', get_cmap('coolwarm')(np.linspace(0, 0.5, 256))
)

# coolwarm 컬러맵의 오른쪽 절반만 사용
coolwarm_right = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_right', get_cmap('coolwarm')(np.linspace(0.5, 1.0, 256))
)

# Set up the plot
fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(dm.cm2in(14), dm.cm2in(7)))
plt.subplots_adjust(left=0.1, right=0.9, top=0.9, bottom=0.15, wspace=0.1, hspace=0.1)

# 메인 축을 기준으로 divider 생성
divider = make_axes_locatable(ax)

# Fontsize
label_fontsize = dm.fs(0.5)
tick_fontsize = dm.fs(-0.5)
cbar_fontsize = dm.fs(-1.5)
cbar_title_fontsize = dm.fs(-1.3)
setpoint_fontsize = dm.fs(-1.3)

# Common setting
label_pad = 8
line_width = 0.6

# Normalize for colorbar
norm_cooling = mcolors.Normalize(vmin=-5, vmax=20)
norm_heating = mcolors.Normalize(vmin=2, vmax=38)

# Scatter plot
cax1 = divider.append_axes("right", size="3%", pad=0.2)
sc1 = ax.scatter(Toa_cooling_list_filtered, 
                 [load / 511 for load in cooling_load_list_filtered], 
                 c=[eff * 100 for eff in ASHP_cooling_exergy_effi_filtered],
                 cmap=coolwarm_left.reversed(), 
                 s=3.0, alpha=0.9, norm=norm_cooling,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar1 = fig.colorbar(sc1, cax=cax1)
cbar1.set_ticks(np.arange(-5, 21, 5))
cbar1.ax.tick_params(labelsize=cbar_fontsize)
cbar1.ax.text(0.5, 1.03, 'Cooling', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar1.ax.transAxes)
cbar1.ax.minorticks_off()

cax2 = divider.append_axes("right", size="3%", pad=0.4)
sc2 = ax.scatter(Toa_heating_list_filtered, 
                 [load / 511 for load in heating_load_list_filtered], 
                 c=[eff * 100 for eff in ASHP_heating_exergy_effi_filtered], 
                 cmap=coolwarm_right, 
                 s=3.0, alpha=0.9, norm=norm_heating,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar2 = fig.colorbar(sc2, cax=cax2)
cbar2.set_ticks(np.arange(2, 39, 9))
cbar2.ax.tick_params(labelsize=cbar_fontsize)
cbar2.set_label('Exergy efficiency [%]', fontsize=cbar_fontsize, labelpad=label_pad)
cbar2.ax.text(0.5, 1.03, 'Heating', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar2.ax.transAxes)
cbar2.ax.minorticks_off()

ax.axvline(x=22, color='dm.teal6', linestyle='--', linewidth=line_width, label='Setpoint temperature')
ax.text(20.5, 46, 'Setpoint temperature', rotation=90, fontsize=setpoint_fontsize, color='dm.teal6', ha='left', va='center')

# limit
ax.set_xlim(-10, 35)
ax.set_ylim(0, 60)

# label
ax.set_xlabel('Environmental temperature [ºC]', fontsize=label_fontsize)
ax.set_ylabel('Thermal energy demand [W/m²]', fontsize=label_fontsize, labelpad=label_pad)

# Tick
ax.set_xticks(np.arange(-10, 36, 5))
ax.set_yticks(np.arange(0, 61, 10))
ax.tick_params(axis='both', which='major', labelsize=tick_fontsize)
ax.tick_params(axis='both', which='minor', labelsize=tick_fontsize)

ax.grid(True)

# plt.savefig('figure/thermal_energy_load.png', dpi=600)
dm.util.save_and_show(fig)

In [48]:
# coolwarm 컬러맵의 왼쪽 절반만 사용
coolwarm_left = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_left', get_cmap('coolwarm')(np.linspace(0, 0.5, 256))
)

# coolwarm 컬러맵의 오른쪽 절반만 사용
coolwarm_right = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_right', get_cmap('coolwarm')(np.linspace(0.5, 1.0, 256))
)

# Set up the plot
fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(dm.cm2in(14), dm.cm2in(7)))
plt.subplots_adjust(left=0.1, right=0.9, top=0.9, bottom=0.15, wspace=0.1, hspace=0.1)

# 메인 축을 기준으로 divider 생성
divider = make_axes_locatable(ax)

# Fontsize
label_fontsize = dm.fs(0.5)
tick_fontsize = dm.fs(-0.5)
cbar_fontsize = dm.fs(-1.5)
cbar_title_fontsize = dm.fs(-1.3)
setpoint_fontsize = dm.fs(-1.3)

# Common setting
label_pad = 8
line_width = 0.6

# Normalize for colorbar
norm_cooling = mcolors.Normalize(vmin=-5, vmax=20)
norm_heating = mcolors.Normalize(vmin=2, vmax=38)

# Scatter plot
cax1 = divider.append_axes("right", size="3%", pad=0.2)
sc1 = ax.scatter(Toa_cooling_list_filtered, 
                 [load for load in exergy_cooling_load_list_filtered], 
                 c=[eff * 100 for eff in ASHP_cooling_exergy_effi_filtered],
                 cmap=coolwarm_left.reversed(), 
                 s=3.0, alpha=0.9, norm=norm_cooling,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar1 = fig.colorbar(sc1, cax=cax1)
cbar1.set_ticks(np.arange(-5, 21, 5))
cbar1.ax.tick_params(labelsize=cbar_fontsize)
cbar1.ax.text(0.5, 1.03, 'Cooling', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar1.ax.transAxes)
cbar1.ax.minorticks_off()

cax2 = divider.append_axes("right", size="3%", pad=0.4)
sc2 = ax.scatter(Toa_heating_list_filtered, 
                 [load for load in exergy_heating_load_list_filtered], 
                 c=[eff * 100 for eff in ASHP_heating_exergy_effi_filtered], 
                 cmap=coolwarm_right, 
                 s=3.0, alpha=0.9, norm=norm_heating,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar2 = fig.colorbar(sc2, cax=cax2)
cbar2.set_ticks(np.arange(2, 39, 9))
cbar2.ax.tick_params(labelsize=cbar_fontsize)
cbar2.set_label('Exergy efficiency [%]', fontsize=cbar_fontsize, labelpad=label_pad)
cbar2.ax.text(0.5, 1.03, 'Heating', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar2.ax.transAxes)
cbar2.ax.minorticks_off()

ax.axvline(x=22, color='dm.teal6', linestyle='--', linewidth=line_width, label='Setpoint temperature')
ax.text(20.5, 3.6, 'Setpoint temperature', rotation=90, fontsize=setpoint_fontsize, color='dm.teal6', ha='left', va='center')

# limit
ax.set_xlim(-10, 35)
ax.set_ylim(-1, 5)

# label
ax.set_xlabel('Environmental temperature [ºC]', fontsize=label_fontsize)
ax.set_ylabel('Exergy demand [W/m²]', fontsize=label_fontsize, labelpad=label_pad)

# Tick
ax.set_xticks(np.arange(-10, 36, 5))
ax.set_yticks(np.arange(-1, 6, 1))
ax.tick_params(axis='both', which='major', labelsize=tick_fontsize)
ax.tick_params(axis='both', which='minor', labelsize=tick_fontsize)

ax.grid(True)

plt.savefig('figure/exergy_load.png', dpi=600)
dm.util.save_and_show(fig)

# Annual ASHP Exergy 논문용 Figure

## Fontsize 지정

In [18]:
plt.rcParams['font.size'] = 9

fs = {
    'label': dm.fs(0),
    'tick': dm.fs(-1.5),
    'legend': dm.fs(-2.0),
    'subtitle': dm.fs(-0.5),
    'cbar_tick': dm.fs(-2.0),
    'cbar_label': dm.fs(-2.0),
    'cbar_title': dm.fs(-1),
    'setpoint': dm.fs(-1),
    'text': dm.fs(-3.0),
            }

pad = {
    'label': 6,
    'tick': 5,
}

LW = np.arange(0.25, 3.0, 0.25)

## Fig. 3 환경온도 + 부하 시뮬레이션 결과

In [19]:
# Set up the subplots
fig, ax = plt.subplots(2, 1, figsize=(dm.cm2in(17), dm.cm2in(11)))
plt.subplots_adjust(left=0.08, right=0.95, top=0.95, bottom=0.1, hspace=0.25)

# Colors
color_temp = 'dm.green4'
color_cooling = 'dm.blue6'
color_heating = 'dm.red6'

# Common settings
line_width = 0.8

# Plot environmental temperature
ax[0].plot(Toa_list, color=color_temp, label='Environmental temperature [$^{\circ}$C]', linewidth=line_width, alpha=0.7)
ax[0].set_ylabel('Environmental temperature [$^{\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
ax[0].tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
ax[0].set_xticks(np.linspace(0, 8760, 7))
ax[0].set_yticks(np.arange(-10, 41, 10))
ax[0].grid(True, linestyle='--', alpha=0.6)
ax[0].text(0.01, 0.97, '(a)', transform=ax[0].transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# Plot loads
ax[1].plot(cooling_load_list / 1000, color=color_cooling, label='Cooling load [kW]', linewidth=line_width, alpha=0.5)
ax[1].plot(heating_load_list / 1000, color=color_heating, label='Heating load [kW]', linewidth=line_width, alpha=0.5)
ax[1].set_xlabel('Hour of year [h]', fontsize=fs['label'], labelpad=pad['label'])
ax[1].set_ylabel('Load [kW]', fontsize=fs['label'], labelpad=pad['label'] + 2)
ax[1].tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
ax[1].set_xticks(np.linspace(0, 8760, 7))
ax[1].set_yticks(np.arange(0, 31, 10))
ax[1].grid(True, linestyle='--', alpha=0.6)
ax[1].text(0.01, 0.97, '(b)', transform=ax[1].transAxes,
           fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')
ax[1].legend(
    labels=['Cooling load', 'Heating load'],
    loc='upper right', ncol=2, frameon=False,
    fontsize=fs['legend'], fancybox=False,
    columnspacing=1.00, labelspacing=0.8,
    bbox_to_anchor=(0.97, 0.995),
    handlelength=1.8
)

# Save and show the figure
plt.savefig('figure/Fig. 3.png', dpi=600)
plt.savefig('figure/Fig. 3.pdf', dpi=600)
dm.util.save_and_show(fig)

## Fig. 6 냉난방 COP 그래프

In [20]:
# parameter
T_ev_l = 12
COP_ref = 4.0

# 2d grid for cooling
PLR_cooling = np.linspace(0.2, 1.0, 500)
T_cond_e_cooling = np.linspace(15, 35, 500)
PLR_grid_cooling, T_cond_e_grid_cooling = np.meshgrid(PLR_cooling, T_cond_e_cooling)

# calculate COP for cooling
EIRFTemp_cooling = 0.38 + 0.02 * T_ev_l + 0 * T_ev_l**2 + 0.01 * T_cond_e_grid_cooling + 0 * T_cond_e_grid_cooling**2 + 0 * T_ev_l * T_cond_e_grid_cooling
EIRFPLR_cooling = 0.22 + 0.50 * PLR_grid_cooling + 0.26 * PLR_grid_cooling**2
COP_cooling = PLR_grid_cooling * COP_ref / (EIRFTemp_cooling * EIRFPLR_cooling)

# 2d grid for heating
PLR_heating = np.linspace(0.2, 1.0, 500)
T_0_heating = np.linspace(-15, 25, 500)
PLR_grid_heating, T_0_grid_heating = np.meshgrid(PLR_heating, T_0_heating)

# calculate COP for heating
COP_heating = -7.46 * (PLR_grid_heating - 0.0047 * T_0_grid_heating - 0.477) ** 2 + 0.0941 * T_0_grid_heating + 4.34

In [21]:
# coolwarm 컬러맵의 왼쪽 절반만 사용
coolwarm_left = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_left', get_cmap('coolwarm')(np.linspace(0, 0.45, 256))
)

# coolwarm 컬러맵의 오른쪽 절반만 사용
coolwarm_right = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_right', get_cmap('coolwarm')(np.linspace(0.55, 1.0, 256))
)

# Set up the figure and axes
fig, (ax_cooling, ax_heating) = plt.subplots(1, 2, figsize=(dm.cm2in(17), dm.cm2in(7)))
plt.subplots_adjust(left=0.08, right=0.98, top=0.9, bottom=0.18, wspace=0.25)

# color
contour_cooling_color = 'dm.white'
contour_heating_color = 'dm.white'

# normalize for colorbar
norm_COP_cooling = mcolors.Normalize(vmin=0.0, vmax=6.0)
norm_COP_heating = mcolors.Normalize(vmin=0.0, vmax=7.0)

# Cooling colormap
colormap_cooling = ax_cooling.pcolormesh(T_cond_e_grid_cooling, PLR_grid_cooling, COP_cooling,
                                         shading='auto',
                                         cmap=coolwarm_left.reversed(),
                                         norm=norm_COP_cooling,
                                         rasterized=True)
cbar_cooling = fig.colorbar(colormap_cooling, ax=ax_cooling)
cbar_cooling.set_label('COP [ - ]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar_cooling.ax.tick_params(labelsize=fs['cbar_tick'])
cbar_cooling.set_ticks(np.arange(0.0, 6.1, 1.0))
cbar_cooling.ax.minorticks_off()

# Cooling contour lines
contour_lines_cooling = ax_cooling.contour(T_cond_e_grid_cooling, PLR_grid_cooling, COP_cooling,
                                           levels=np.arange(3.0, 5.6, 0.5), 
                                           colors=contour_cooling_color,
                                           linewidths=0.7,
                                           alpha=0.9)
ax_cooling.clabel(contour_lines_cooling, 
                  inline=True, 
                  fontsize=fs['tick'],
                  fmt='%.1f')

# Cooling graph
ax_cooling.set_xlabel('Environmental temperature [$^{\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
ax_cooling.set_ylabel('Part load ratio [ - ]', fontsize=fs['label'], labelpad=pad['label'])
ax_cooling.set_xlim(15, 35)
ax_cooling.set_ylim(0.2, 1.0)
ax_cooling.tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
ax_cooling.tick_params(axis='both', which='minor', labelsize=fs['tick'], pad=pad['tick'])
ax_cooling.set_xticks(np.arange(15, 36, 5))
ax_cooling.set_yticks(np.arange(0.2, 1.1, 0.2))
ax_cooling.text(0.02, 1.09, '(a) Cooling mode', transform=ax_cooling.transAxes,
                fontsize=fs['subtitle'], va='top', ha='left')

# Heating colormap
colormap_heating = ax_heating.pcolormesh(T_0_grid_heating, PLR_grid_heating, COP_heating,
                                         shading='auto',
                                         cmap=coolwarm_right,
                                         norm=norm_COP_heating,
                                         rasterized=True)
cbar_heating = fig.colorbar(colormap_heating, ax=ax_heating)
cbar_heating.set_label('COP [ - ]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar_heating.ax.tick_params(labelsize=fs['cbar_tick'])
cbar_heating.set_ticks(np.arange(0.0, 7.1, 1.0))
cbar_heating.ax.minorticks_off()

# Heating contour lines
contour_lines_heating = ax_heating.contour(T_0_grid_heating, PLR_grid_heating, COP_heating,
                                           levels=np.arange(1.0, 7.1, 1.0),
                                           colors=contour_heating_color,
                                           linewidths=0.7,
                                           alpha=0.9)
ax_heating.clabel(contour_lines_heating, 
                  inline=True, 
                  fontsize=fs['tick'],
                  fmt='%.1f')

# Heating graph
ax_heating.set_xlabel('Environmental temperature [$^{\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
ax_heating.set_ylabel('Part load ratio [ - ]', fontsize=fs['label'], labelpad=pad['label'])
ax_heating.set_xlim(-10, 25)
ax_heating.set_ylim(0.2, 1.0)
ax_heating.tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
ax_heating.tick_params(axis='both', which='minor', labelsize=fs['tick'], pad=pad['tick'])
ax_heating.set_xticks(np.arange(-15, 26, 10))
ax_heating.set_yticks(np.arange(0.2, 1.1, 0.2))
ax_heating.text(0.01, 1.09, '(b) Heating mode', transform=ax_heating.transAxes,
                fontsize=fs['subtitle'], va='top', ha='left')

# # Save and show the figure
# plt.savefig('figure/Fig. 6.png', dpi=600)
plt.savefig('figure/Fig. 6.svg', dpi=600, transparent=True)
dm.util.save_and_show(fig)

## Fig. 7 Fan 특성곡선

In [22]:
fan_model = enex.Fan()

# 유량 범위
int_flow_range = np.linspace(1.0, 3.0, 100)
ext_flow_range = np.linspace(1.5, 3.5, 100)

# Common settings
line_width = 1.0

# Color
colors = ['dm.soft blue', 'dm.cool green', 'dm.red5']

fig, axes = plt.subplots(2, 1, figsize=(dm.cm2in(9), dm.cm2in(12)))
plt.subplots_adjust(left=0.12, right=0.7, top=0.92, bottom=0.1, wspace=0.9, hspace=0.5)

fan_labels = ['Indoor unit', 'Outdoor unit']
flow_ranges = [int_flow_range, ext_flow_range]
ylim_pressure = [(130, 210), (250, 370)]
yticks_pressure = [np.linspace(130, 210, 5), np.linspace(250, 370, 5)]
ylim_efficiency = [(50, 70), (50, 70)]
yticks_efficiency = [np.linspace(50, 70, 5), np.linspace(50, 70, 5)]
ylim_power = [(200, 1200), (600, 2200)]
yticks_power = [np.linspace(200, 1200, 5), np.linspace(600, 2200, 5)]
xlims = [(1.0, 3.0), (1.5, 3.5)]
xticks = [np.arange(1.0, 3.1, 0.5), np.arange(1.5, 3.6, 0.5)]

for ax, fan, label, flow_range, ylim_p, yticks_p, ylim_e, yticks_e, ylim_pow, yticks_pow, xlim, xtick in zip(
    axes, fan_model.fan_list, fan_labels, flow_ranges, ylim_pressure, yticks_pressure, ylim_efficiency, yticks_efficiency, ylim_power, yticks_power, xlims, xticks
):
    pressure = fan_model.get_pressure(fan, flow_range)
    efficiency = fan_model.get_efficiency(fan, flow_range)
    power = fan_model.get_power(fan, flow_range)

    # Efficiency - Left y-axis
    ax.set_xlabel('Air flow rate [m$^3$/s]', fontsize=fs['label'], labelpad=pad['label'])
    ax.set_ylabel('Efficiency [%]', color=colors[1], fontsize=fs['label'], labelpad=pad['label'])
    eff_line, = ax.plot(flow_range, efficiency * 100, color=colors[1], linestyle='-', label='Efficiency', linewidth=line_width)
    ax.tick_params(axis='x', labelsize=fs['tick'], pad=pad['tick'])
    ax.tick_params(axis='y', labelsize=fs['tick'], colors=colors[1], pad=pad['tick'])
    ax.set_xlim(xlim)
    ax.set_xticks(xtick)
    ax.set_ylim(ylim_e)
    ax.set_yticks(yticks_e)
    ax.spines['left'].set_color(colors[1])

    # Power - First right y-axis
    ax2 = ax.twinx()
    ax2.set_ylabel('Power [W]', color=colors[2], fontsize=fs['label'], labelpad=pad['label'])
    power_line, = ax2.plot(flow_range, power, color=colors[2], linestyle=':', label='Power', linewidth=line_width)
    ax2.tick_params(axis='y', labelsize=fs['tick'], colors=colors[2], pad=pad['tick'])
    ax2.set_ylim(ylim_pow)
    ax2.set_yticks(yticks_pow)
    ax2.spines['top'].set_visible(False)
    ax2.spines['bottom'].set_visible(False)
    ax2.spines['left'].set_visible(False)
    ax2.spines['right'].set_color(colors[2])

    # Pressure drop - Second right y-axis
    ax3 = ax.twinx()
    ax3.spines['right'].set_position(('axes', 1.28))
    ax3.set_ylabel('Pressure drop [Pa]', color=colors[0], fontsize=fs['label'], labelpad=pad['label'])
    pressure_line, = ax3.plot(flow_range, pressure, color=colors[0], linestyle='--', label='Pressure drop', linewidth=line_width)
    ax3.tick_params(axis='y', labelsize=fs['tick'], colors=colors[0], pad=pad['tick'])
    ax3.set_ylim(ylim_p)
    ax3.set_yticks(yticks_p)
    ax3.spines['top'].set_visible(False)
    ax3.spines['bottom'].set_visible(False)
    ax3.spines['left'].set_visible(False)
    ax3.spines['right'].set_color(colors[0])

    ax.grid(True)

    # remove minor ticks
    ax.tick_params(axis='x', which='minor', bottom=False)
    ax.tick_params(axis='y', which='minor', left=False)
    ax.tick_params(axis='y', which='minor', right=False)
    ax2.tick_params(axis='y', which='minor', right=False)
    ax3.tick_params(axis='y', which='minor', right=False)

    # Add titles to each subplot
    ax.text(0.01, 1.13, f'({chr(97 + axes.tolist().index(ax))}) {label} fan',
            transform=ax.transAxes, fontsize=fs['subtitle'], va='top', ha='left')

    # Add legend
    lines = [eff_line, power_line, pressure_line]
    labels_ = [line.get_label() for line in lines]
    ax.legend([pressure_line, eff_line, power_line], 
              ['Pressure drop', 'Efficiency', 'Power'], 
              loc='upper left', fontsize=fs['legend'])

# Save and show
plt.savefig('figure/Fig. 7.png', dpi=600)
plt.savefig('figure/Fig. 7.pdf', dpi=600)
dm.util.save_and_show(fig)


## Fig. 9 Energy efficiency 격자 형태

In [23]:
# 컬러맵 설정
coolwarm_left = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_left', cm.get_cmap('coolwarm')(np.linspace(0, 0.45, 256))
)
coolwarm_right = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_right', cm.get_cmap('coolwarm')(np.linspace(0.55, 1.0, 256))
)

# Common settings
bin_temp = 2.5   # 온도 격자 크기
bin_load = 5     # 부하 격자 크기
x_range = (-10, 35)
y_range = (0, 30)
line_width = 1.0
cooling_cop_white_text = 3.65
heating_cop_white_text = 3.65

# Function to calculate average COP in each grid
def grid_stats(Toa, Load, COP, bins_x, bins_y):
    avg_COP = np.full((len(bins_y)-1, len(bins_x)-1), np.nan)
    for i in range(len(bins_x)-1):      # x축 (Toa)
        for j in range(len(bins_y)-1):  # y축 (Load)
            mask = (
                (Toa >= bins_x[i]) & (Toa < bins_x[i+1]) &
                (Load >= bins_y[j]) & (Load < bins_y[j+1])
            )
            if np.any(mask):
                avg_COP[j,i] = np.mean(COP[mask])
    return avg_COP, bins_x, bins_y

# Data
# Cooling
Toa_c = np.array(Toa_cooling_list_filtered)
Load_c = np.array(cooling_load_list_filtered) / 1000 
COP_c = np.array(ASHP_cooling_COP_filtered)
# Heating
Toa_h = np.array(Toa_heating_list_filtered)
Load_h = np.array(heating_load_list_filtered) / 1000
COP_h = np.array(ASHP_heating_COP_filtered)

# Bins
bins_x = np.arange(x_range[0], x_range[1]+bin_temp, bin_temp)
bins_y = np.arange(y_range[0], y_range[1]+bin_load, bin_load)

# Calculate average COP in each grid
avg_c, xedges, yedges = grid_stats(Toa_c, Load_c, COP_c, bins_x, bins_y)
avg_h, _, _ = grid_stats(Toa_h, Load_h, COP_h, bins_x, bins_y)

# Plot
fig, axes = plt.subplots(2, 1, figsize=(dm.cm2in(17), dm.cm2in(13)), sharex=False, sharey=True)
plt.subplots_adjust(left=0.07, right=1.07, top=0.95, bottom=0.08, hspace=0.25)  

# Cooling plot
im1 = axes[0].pcolormesh(xedges, yedges, avg_c, cmap=coolwarm_left.reversed(), vmin=1.5, vmax=4.0)
for i in range(len(xedges)-1):
    for j in range(len(yedges)-1):
        # 격자 테두리 추가
        rect = plt.Rectangle(
            (xedges[i], yedges[j]),
            xedges[i+1] - xedges[i],
            yedges[j+1] - yedges[j],
            linewidth=line_width,
            edgecolor='white',
            facecolor='none',
            zorder=1
        )
        axes[0].add_patch(rect)
        if not np.isnan(avg_c[j,i]):
            text_color = 'white' if avg_c[j,i] >= cooling_cop_white_text else 'black'
            axes[0].text((xedges[i]+xedges[i+1])/2, (yedges[j]+yedges[j+1])/2,
                         f"{avg_c[j,i]:.1f}",
                         ha='center', va='center', fontsize=fs['text'], color=text_color)
axes[0].set_ylabel('Cooling load [kW]', fontsize=fs['label'], labelpad=pad['label'])
axes[0].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[0].minorticks_off()
cbar1 = fig.colorbar(im1, ax=axes[0], label='Energy efficiency (COP$_{sys}$) [ - ]', orientation='vertical', pad=0.02, aspect=20)
cbar1.set_label('Energy efficiency (COP$_{sys}$) [ - ]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar1.ax.tick_params(axis='both', which='major', labelsize=fs['cbar_tick'])
cbar1.ax.tick_params(axis='both', which='minor', bottom=False, left=False)
cbar1.ax.minorticks_off()
axes[0].axvline(x=22, color='dm.teal6', linestyle='--', linewidth=0.6, label='Setpoint')
axes[0].text(20.8, 26.2, 'Setpoint', rotation=90, fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='center')
axes[0].text(0.01, 0.97, '(a)', transform=axes[0].transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# Heating plot
im2 = axes[1].pcolormesh(xedges, yedges, avg_h, cmap=coolwarm_right, vmin=1.5, vmax=4.0)
for i in range(len(xedges)-1):
    for j in range(len(yedges)-1):
        # 격자 테두리 추가
        rect = plt.Rectangle(
            (xedges[i], yedges[j]),
            xedges[i+1] - xedges[i],
            yedges[j+1] - yedges[j],
            linewidth=line_width,
            edgecolor='dm.white',
            facecolor='none',
            zorder=1
        )
        axes[1].add_patch(rect)
        if not np.isnan(avg_h[j,i]):
            text_color = 'white' if avg_h[j,i] >= heating_cop_white_text else 'black'
            axes[1].text((xedges[i]+xedges[i+1])/2, (yedges[j]+yedges[j+1])/2,
                         f"{avg_h[j,i]:.1f}",
                         ha='center', va='center', fontsize=fs['text'], color=text_color)
axes[1].set_ylabel('Heating load [kW]', fontsize=fs['label'], labelpad=pad['label'])
axes[1].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[1].minorticks_off()
cbar2 = fig.colorbar(im2, ax=axes[1], label='Energy efficiency (COP$_{sys}$) [ - ]', orientation='vertical', pad=0.02, aspect=20)
cbar2.set_label('Energy efficiency (COP$_{sys}$) [ - ]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar2.ax.tick_params(axis='both', which='major', labelsize=fs['cbar_tick'])
cbar2.ax.tick_params(axis='both', which='minor', bottom=False, left=False)
cbar2.ax.minorticks_off()
axes[1].axvline(x=22, color='dm.teal6', linestyle='--', linewidth=0.6, label='Setpoint')
axes[1].text(20.8, 26.2, 'Setpoint', rotation=90, fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='center')
axes[1].text(0.01, 0.97, '(b)', transform=axes[1].transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# Common settings
for ax in axes:
    ax.set_xlim(x_range)
    ax.set_ylim(y_range)
    ax.set_xlabel('Environmental temperature [$^{\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
    ax.grid(True, linestyle='--', alpha=0.5)
    ax.set_xticks(xedges, minor=True)
    ax.tick_params(axis='x', which='minor', length=1.6, color='dm.gray7', pad=pad['tick'])

plt.savefig('figure/Fig. 9.png', dpi=600)
plt.savefig('figure/Fig. 9.pdf', dpi=600)
dm.util.save_and_show(fig)

## Fig. 10 Exergy efficiency 격자 형태

In [24]:
# 컬러맵 설정
coolwarm_left = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_left', cm.get_cmap('coolwarm')(np.linspace(0, 0.45, 256))
)
coolwarm_right = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_right', cm.get_cmap('coolwarm')(np.linspace(0.55, 1.0, 256))
)

# Common settings
bin_temp = 2.5   # 온도 격자 크기
bin_load = 5     # 부하 격자 크기
x_range = (-10, 35)
y_range = (0, 30)
line_width = 1.0
cooling_X_eff_white_text = 18.0
heating_X_eff_white_text = 26.8

# Function to calculate average X_eff in each grid
def grid_stats(Toa, Load, X_eff, bins_x, bins_y):
    avg_X_eff = np.full((len(bins_y) - 1, len(bins_x) - 1), np.nan)
    for i in range(len(bins_x) - 1):      # x축 (Toa)
        for j in range(len(bins_y) - 1):  # y축 (Load)
            mask = (
                (Toa >= bins_x[i]) & (Toa < bins_x[i + 1]) &
                (Load >= bins_y[j]) & (Load < bins_y[j + 1])
            )
            if np.any(mask):
                avg_X_eff[j, i] = np.mean(X_eff[mask])
    return avg_X_eff, bins_x, bins_y

# Cooling / Heating 데이터
Toa_c = np.array(Toa_cooling_list_filtered)
Load_c = np.array(cooling_load_list_filtered) / 1000
X_eff_c = np.array(ASHP_cooling_exergy_effi_filtered) * 100  # [%]로 변환

Toa_h = np.array(Toa_heating_list_filtered)
Load_h = np.array(heating_load_list_filtered) / 1000
X_eff_h = np.array(ASHP_heating_exergy_effi_filtered) * 100  # [%]로 변환

# Bins
bins_x = np.arange(x_range[0], x_range[1] + bin_temp, bin_temp)
bins_y = np.arange(y_range[0], y_range[1] + bin_load, bin_load)

# Calculate average X_eff(엑서지 효율) in each grid
avg_c, xedges, yedges = grid_stats(Toa_c, Load_c, X_eff_c, bins_x, bins_y)
avg_h, _, _ = grid_stats(Toa_h, Load_h, X_eff_h, bins_x, bins_y)

# Plot
fig, axes = plt.subplots(2, 1, figsize=(dm.cm2in(17), dm.cm2in(13)), sharex=False, sharey=True)
plt.subplots_adjust(left=0.07, right=1.07, top=0.95, bottom=0.08, hspace=0.25)

# --- Cooling plot ---
im1 = axes[0].pcolormesh(xedges, yedges, avg_c, cmap=coolwarm_left.reversed(), vmin=0, vmax=20)

for i in range(len(xedges) - 1):
    for j in range(len(yedges) - 1):
        rect = plt.Rectangle(
            (xedges[i], yedges[j]),
            xedges[i + 1] - xedges[i],
            yedges[j + 1] - yedges[j],
            linewidth=line_width,
            edgecolor='white',
            facecolor='none',
            zorder=1
        )
        axes[0].add_patch(rect)
        if not np.isnan(avg_c[j, i]):
            text_color = 'white' if avg_c[j, i] >= cooling_X_eff_white_text else 'black'
            axes[0].text(
                (xedges[i] + xedges[i + 1]) / 2,
                (yedges[j] + yedges[j + 1]) / 2,
                f"{avg_c[j, i]:.1f}",
                ha='center', va='center',
                fontsize=fs['text'],
                color=text_color
            )

axes[0].set_ylabel('Cooling load [kW]', fontsize=fs['label'], labelpad=pad['label'])
axes[0].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[0].minorticks_off()

cbar1 = fig.colorbar(
    im1, ax=axes[0],
    label='Exergy efficiency ($\\eta_{X,sys}$) [%]',
    orientation='vertical', pad=0.02, aspect=20
)
cbar1.set_label('Exergy efficiency ($\\eta_{X,sys}$) [%]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar1.set_ticks(np.arange(0, 21, 5))
cbar1.ax.tick_params(axis='both', which='major', labelsize=fs['cbar_tick'])
cbar1.ax.tick_params(axis='both', which='minor', bottom=False, left=False)
cbar1.ax.minorticks_off()

axes[0].axvline(x=22, color='dm.teal6', linestyle='--', linewidth=0.6, label='Setpoint')
axes[0].text(20.8, 26.2, 'Setpoint', rotation=90, fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='center')
axes[0].text(0.01, 0.97, '(a)', transform=axes[0].transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# --- Heating plot ---
im2 = axes[1].pcolormesh(xedges, yedges, avg_h, cmap=coolwarm_right, vmin=0, vmax=32)

for i in range(len(xedges) - 1):
    for j in range(len(yedges) - 1):
        rect = plt.Rectangle(
            (xedges[i], yedges[j]),
            xedges[i + 1] - xedges[i],
            yedges[j + 1] - yedges[j],
            linewidth=line_width,
            edgecolor='dm.white',
            facecolor='none',
            zorder=1
        )
        axes[1].add_patch(rect)
        if not np.isnan(avg_h[j, i]):
            text_color = 'white' if avg_h[j, i] >= heating_X_eff_white_text else 'black'
            axes[1].text(
                (xedges[i] + xedges[i + 1]) / 2,
                (yedges[j] + yedges[j + 1]) / 2,
                f"{avg_h[j, i]:.1f}",
                ha='center', va='center',
                fontsize=fs['text'],
                color=text_color
            )

axes[1].set_ylabel('Heating load [kW]', fontsize=fs['label'], labelpad=pad['label'])
axes[1].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[1].minorticks_off()

cbar2 = fig.colorbar(
    im2, ax=axes[1],
    label='Exergy efficiency ($\\eta_{X,sys}$) [%]',
    orientation='vertical', pad=0.02, aspect=20
)
cbar2.set_label('Exergy efficiency ($\\eta_{X,sys}$) [%]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar2.set_ticks(np.arange(0, 33, 8))
cbar2.ax.tick_params(axis='both', which='major', labelsize=fs['cbar_tick'])
cbar2.ax.tick_params(axis='both', which='minor', bottom=False, left=False)
cbar2.ax.minorticks_off()

axes[1].axvline(x=22, color='dm.teal6', linestyle='--', linewidth=0.6, label='Setpoint')
axes[1].text(20.8, 26.2, 'Setpoint', rotation=90, fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='center')
axes[1].text(0.01, 0.97, '(b)', transform=axes[1].transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# --- Common settings ---
for ax in axes:
    ax.set_xlim(x_range)
    ax.set_ylim(y_range)
    ax.set_xlabel('Environmental temperature [$^{\\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
    ax.grid(True, linestyle='--', alpha=0.5)
    ax.set_xticks(xedges, minor=True)
    ax.tick_params(axis='x', which='minor', length=1.6, color='dm.gray7')

plt.savefig('figure/Fig. 10.png', dpi=600)
plt.savefig('figure/Fig. 10.pdf', dpi=600)
dm.util.save_and_show(fig)

## Fig. 11 Net exergy

In [36]:
from matplotlib.ticker import AutoMinorLocator  # 파일 상단 또는 이 블록 위

# 원하는 마이너 틱 개수(축별)
x_minor_between = 1   # X축: 메이저 틱 사이 마이너 1개
y_minor_between = 1   # Y축: 메이저 틱 사이 마이너 1개

xmin, xmax, xint, xmar = -10, 40, 5, 0
ymin, ymax, yint, ymar =  0, 6, 1, 0

# constant
c_a = 1005 # Specific heat capacity of air [J/kgK]
rho_a = 1.225 # Density of air [kg/m³]
k_a = 0.0257 # Thermal conductivity of air [W/mK]

T_range = np.arange(xmin, xmax+xint, 0.1)
T_a_int_in = 22

T0_cooling = -6
T0_heating = 33
T0 = np.array([T0_cooling, T0_heating])

T_range_K = enex.C2K(T_range)
T0_K = enex.C2K(T0)

dV_int_unit = 1 # 환기량 [m³/s]
y1 = c_a * rho_a * dV_int_unit * ((T_range_K - T0_K[0]) - T0_K[0] * np.log(T_range_K / T0_K[0]))*enex.W2kW
y2 = c_a * rho_a * dV_int_unit * ((T_range_K - T0_K[1]) - T0_K[1] * np.log(T_range_K / T0_K[1]))*enex.W2kW

T_set = 22
T_a_int_out_cooling = 12
T_a_int_out_heating = 32

# 3) Figure 생성
fig = plt.figure(
    figsize=(dm.cm2in(14), dm.cm2in(7)),
    dpi=300
)

# 4) GridSpec 레이아웃
nrows, ncols = 1, 1
gs = fig.add_gridspec(
    nrows=nrows, ncols=ncols,
    left=0.16, right=0.98, top=0.96, bottom=0.18,
    hspace=0.10, wspace=0.10
)

# 5) 2중 for 문으로 축 생성 및 순회 (단일 플롯이어도 유지)
for row in range(nrows):
    for col in range(ncols):
        ax = fig.add_subplot(gs[row, col])

        # 6) 데이터 플로팅 (계단형 라인)
        lw = 1
        line1, = ax.plot(
            T_range, y1, 
            c='dm.red4', lw=lw, label=f'Outdoor air temp = - {abs(T0_cooling)} °C (winter)',
        )
        line2, = ax.plot(
            T_range, y2,
            c='dm.blue3', lw=lw, label=f'Outdoor air temp = {T0_heating} °C (summer)', 
        )
        # T_set°C
        ds_lw = 0.6 # dashed line width
        c1 = 'dm.teal'
        c2 = 'dm.blue'
        c3 = 'dm.red'
        ax.axvline(x=T_set, color=c1 + '6', linestyle='--', linewidth=ds_lw, zorder=0)
        # ax.axvline(x=T_a_int_out_cooling, color=c2 + '6', linestyle='--', linewidth=ds_lw, zorder=0)
        # ax.axvline(x=T_a_int_out_heating, color=c3 + '6', linestyle='--', linewidth=ds_lw, zorder=0)

        dx = -0.3
        ax.text(T_set + dx, ymax*0.97, 'Setpoint', rotation=90,
                fontsize=fs['setpoint'], color=c1 + '6', ha='right', va='top')

        # 교차점 계산 및 scatter plot 추가
        ss = 6 # scatter size
        sc1 = 'dm.red8'
        sc2 = 'dm.blue8'
        y1_at_T_set = np.interp(T_set, T_range, y1)
        y2_at_T_set = np.interp(T_set, T_range, y2)
        ax.scatter([T_set, T_set], [y1_at_T_set, y2_at_T_set], color=[sc1, sc2], s=ss, zorder=5)

        # --- NEW: scatter 위에 y값 표시 ---
        for x, y, col in [(T_set, y1_at_T_set, sc1), (T_set, y2_at_T_set, sc2)]:
            ax.annotate(
                f"{y:.2f}",
                (x, y),
                textcoords="offset points",
                xytext=(0, 4),
                ha="center",
                va="bottom",
                fontsize=fs['setpoint'],
                color=col,
                zorder=6
            )

        # 3번 점선 (x=T_a_int_out_heating)이 line1과 만나는 점
        y1_at_T_a_int_out_heating = np.interp(T_a_int_out_heating, T_range, y1)
        # ax.scatter(T_a_int_out_heating, y1_at_T_a_int_out_heating, color=sc1, s=ss, zorder=5)

        # 2번 점선 (x=T_a_int_out_cooling)이 line2와 만나는 점
        y2_at_T_a_int_out_cooling = np.interp(T_a_int_out_cooling, T_range, y2)
        # ax.scatter(T_a_int_out_cooling, y2_at_T_a_int_out_cooling, color=sc2, s=ss, zorder=5)
        
        y1_dy = y1_at_T_a_int_out_heating - y1_at_T_set
        y2_dy = y2_at_T_a_int_out_cooling - y2_at_T_set

        # 7) 축/눈금/범위 등 그래프 요소
        ax.set_xlabel('Air temperature [°C]', labelpad=pad['label'], fontsize=fs['label'])
        ax.set_ylabel('Exergy rate in air flow [kW/(m$^3$/s)]', labelpad=pad['label'], fontsize=fs['label'])
        ax.set_xlim(xmin, xmax)
        ax.set_ylim(ymin, ymax)
        ax.set_xticks(np.arange(xmin, xmax + 1, xint))
        ax.set_yticks(np.arange(ymin, ymax + 1, yint))

        # 축 라벨/틱 라벨 사이 패딩과 폰트사이즈
        ax.tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])

        # 마이너 틱 로케이터 설정 (축별로 개수 조절)
        ax.xaxis.set_minor_locator(AutoMinorLocator(x_minor_between + 1))
        ax.yaxis.set_minor_locator(AutoMinorLocator(y_minor_between + 1))

        # (선택) 격자
        ax.grid(True, which='major', alpha=0.25)

        # 8) 범례
        handles = [line1, line2]
        labels = [h.get_label() for h in handles]
        ax.legend(handles, labels, loc='upper left', fontsize=fs['legend'], frameon=False, handletextpad=1)

# 9) 레이아웃 최적화 (tight_layout 사용 금지)
dm.simple_layout(fig)
plt.savefig('figure/Fig. 11.png', dpi=600)
plt.savefig('figure/Fig. 11.pdf', dpi=600, transparent=True)

dm.save_and_show(fig)


## Fig. 12 1월, 4월, 8월, 10월 결과

In [42]:
# 1) 사용할 월과 '월별 시작일로부터 7일' 부분집합 만들기
months_to_plot = [1, 4, 8, 10]
start_map = {1: 9, 4: 10, 8: 7, 10: 10}  # 월별 시작일

day_all = weekday_df['Date/Time_clean'].str.slice(3, 5).astype(int)  # 'MM/DD ...' → DD
month_s = weekday_df['Month']
start_day = month_s.map(start_map)  # 행별 시작일(해당 월 아닌 행은 NaN)

mask = (
    month_s.isin(months_to_plot) &
    day_all.ge(start_day) &
    day_all.le(start_day + 4)  # 시작
)

df_sub = weekday_df.loc[mask].copy()

# 표시/축용 보조 열
df_sub['Day'] = day_all[mask].values
hour_sub = df_sub['Date/Time_clean'].str.slice(6, 8).astype(int)  # '... HH:MM:SS' → HH
df_sub['xpos'] = df_sub['Day'] + hour_sub / 24.0  # 연속 x축

# 최대 부하(정규화용) 한 번만 계산
Q_r_max_cooling = (df_sub['DistrictCooling:Facility [J](TimeStep)'] / 3600.0).max()
Q_r_max_heating = (df_sub['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0).max()

# 2) COP / 엑서지 계산 (부분집합에만 수행)
def compute_metrics(row):
    Toa = row['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)']
    cooling_load = row['DistrictCooling:Facility [J](TimeStep)'] / 3600.0
    heating_load = row['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0

    exergy_effi = 0.0
    cop = 0.0

    if cooling_load > 0:
        ASHP = enex.AirSourceHeatPump_cooling()
        ASHP.T0 = Toa
        ASHP.T_a_room = 22
        ASHP.Q_r_int = cooling_load
        ASHP.Q_r_max = Q_r_max_cooling
        ASHP.system_update()
        if ASHP.X_eff > 0:
            exergy_effi = ASHP.X_eff * 100.0
            cop = ASHP.COP_sys

    elif heating_load > 0:
        ASHP = enex.AirSourceHeatPump_heating()
        ASHP.T0 = Toa
        ASHP.T_a_room = 22
        ASHP.Q_r_int = heating_load
        ASHP.Q_r_max = Q_r_max_heating
        ASHP.system_update()
        if ASHP.X_eff > 0:
            exergy_effi = ASHP.X_eff * 100.0
            cop = ASHP.COP_sys

    return pd.Series({'COP': cop, 'ExergyEff': exergy_effi})

df_sub[['COP', 'ExergyEff']] = df_sub.apply(compute_metrics, axis=1)

In [43]:
from matplotlib.ticker import AutoMinorLocator
import matplotlib.gridspec as gridspec

# Colors
temp_color     = 'dm.green4'   # 외기온
load_heat_color= 'dm.red5'     # 난방 부하
load_cool_color= 'dm.blue5'  # 냉방 부하
cop_color      = 'dm.orange4'    # COP
X_eff_color    = 'dm.gray6'     # 엑서지 효율

# 월 영어 이름
month_name = {1: '(a) January',  8: '(b) August', 4: '(c) April', 10: '(d) October'}

# y축 레이블 정렬을 위한 고정 좌표 (좌/우 동일하게 맞춤)
YLABEL_X_LEFT  = -0.13   # 좌측 y라벨 x좌표 (axes fraction)
YLABEL_X_RIGHT =  1.13   # 우측 y라벨 x좌표
YLABEL_Y       =  0.5    # y라벨 y좌표(세로 중앙)

# layout
layout = [[1, 8],
          [4, 10]]

fig = plt.figure(figsize=(dm.cm2in(17), dm.cm2in(18)))
outer = gridspec.GridSpec(2, 2, figure=fig, wspace=0.55, hspace=0.25)
plt.subplots_adjust(left=0.08, right=0.92, top=0.97, bottom=0.05)

def style_axis_colors(ax_left, ax_right, left_color, right_color):
    """좌/우 축 색상 및 마이너틱 설정, 반대 스파인 숨김"""
    # 서로 반대쪽 스파인은 감추기
    ax_left.spines['right'].set_visible(False)
    ax_right.spines['left'].set_visible(False)

    # 왼쪽 y축
    ax_left.spines['left'].set_color(left_color)
    ax_left.yaxis.label.set_color(left_color)
    ax_left.tick_params(axis='y', which='both', colors=left_color)
    ax_left.yaxis.set_minor_locator(AutoMinorLocator(2))   # 메이저 사이 1개

    # 오른쪽 y축
    ax_right.spines['right'].set_color(right_color)
    ax_right.yaxis.label.set_color(right_color)
    ax_right.tick_params(axis='y', which='both', colors=right_color)
    ax_right.yaxis.set_minor_locator(AutoMinorLocator(2))  # 메이저 사이 1개

def align_ylabel_positions(ax_left, ax_right):
    """좌/우 y축 레이블 좌표를 고정 좌표로 맞춤(두 행/열 모두 동일한 위치)"""
    ax_left.yaxis.set_label_coords(YLABEL_X_LEFT,  YLABEL_Y)
    ax_right.yaxis.set_label_coords(YLABEL_X_RIGHT, YLABEL_Y)

# ------------------------------------------------------------
def plot_one_month(ax_top, ax_bot, mdf, month, start_map):
    """한 달(월) 섹션: 상단(외기온+부하), 하단(COP+엑서지)"""
    start = start_map[month]
    end   = start + 5  # 7일 구간: [start, start+6]

    # ======= 상단: 외기온도(좌, 실선) + 부하(우, 실선) =======
    ax1 = ax_top
    ax2 = ax1.twinx()
    # 부하가 외기온보다 위에 오도록 축/패치/라인 zorder 조정
    ax1.set_zorder(ax2.get_zorder() + 1)   # 우측 축을 좌측 축 위로
    ax1.patch.set_visible(False)           # 좌측 축 배경 비활성화(가림 방지)

    # 부하 (우, 실선) — 월에 따라 난방/냉방 선택
    if month in [1, 10]:
        load_series = mdf['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0 / 1000.0
        load_color  = load_heat_color
        load_label  = 'Heating load [kW]'
    else:  # 4, 8
        load_series = mdf['DistrictCooling:Facility [J](TimeStep)'] / 3600.0 / 1000.0
        load_color  = load_cool_color
        load_label  = 'Cooling load [kW]'

    ax2.fill_between(
        mdf['xpos'],
        0,
        load_series,
        color=load_color,
        alpha=0.3,
        zorder=1,
    )
    ax2.set_ylabel(load_label, fontsize=fs['label'])

    # 외기온 (좌, 실선) — 아래쪽 zorder
    ax1.plot(
        mdf['xpos'],
        mdf['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)'],
        linewidth=0.7,
        color=temp_color,
        zorder=3,
        alpha=1.0
    )

    # Setpoint 라인
    ax1.axhline(y=22, color='dm.teal6', linestyle='--', linewidth=0.7, alpha=0.7, label='Setpoint')
    ax1.text(start + 0.1, 22 + 0.7, 'Setpoint', fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='bottom')

    # 축 범위/눈금
    ax1.set_xlim(start, end)
    ax1.set_ylim(-10, 40); ax1.set_yticks(np.arange(-10, 41, 10))
    ax2.set_ylim(0, 30);   ax2.set_yticks(np.arange(0, 31, 10))

    # 라벨/타이틀 (왼쪽 상단)
    ax1.set_ylabel('Environmental temp. [$^{\circ}$C]', fontsize=fs['label'])
    ax1.set_title(month_name[month], fontsize=fs['subtitle'], loc='left')

    # 상단 x축: 숫자 라벨만 숨기고, 틱(메이저/마이너)은 표시하고 싶다면 아래 두 줄 사용
    ax1.xaxis.set_minor_locator(AutoMinorLocator(2))  # 메이저 사이 1개
    ax1.tick_params(axis='x', which='both', labelsize=fs['tick'], pad=pad['tick'])

    # 축 스타일(색상/마이너틱) + y라벨 좌표 정렬
    style_axis_colors(ax1, ax2, temp_color, load_color)
    align_ylabel_positions(ax1, ax2)

    # y축 폰트/간격
    ax1.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax2.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax1.spines['left'].set_linewidth(0.6)
    ax2.spines['right'].set_linewidth(0.6)

    # ======= 하단: COP(좌, 실선) + 엑서지효율(우, 점선) =======
    ax3 = ax_bot
    ax4 = ax3.twinx()
    ax4.set_zorder(ax3.get_zorder() + 1)
    ax3.patch.set_visible(False)

    # COP (좌, 실선)
    ax3.plot(mdf['xpos'], mdf['COP'], linewidth=0.7, color=cop_color, zorder=2)
    # 엑서지 효율 (우, dashed)
    ax4.plot(mdf['xpos'], mdf['ExergyEff'], linewidth=0.7, linestyle='--', color=X_eff_color, zorder=4)

    # 범위/라벨
    ax3.set_xlim(start, end)
    ax3.set_ylim(0, 5)
    ax4.set_ylim(0, 50)
    ax3.set_ylabel('Energy efficiency [ - ]', fontsize=fs['label'])
    ax4.set_ylabel('Exergy efficiency [%]', fontsize=fs['label'])

    # 하단 x축: 시작~끝 정수 + 마이너틱 1개
    ticks = np.arange(start, end + 1, 1)
    ax3.set_xticks(ticks)
    ax3.set_xticklabels([str(d) for d in ticks], fontsize=fs['tick'])
    ax3.xaxis.set_minor_locator(AutoMinorLocator(2))  # 메이저 사이 1개

    # 축 스타일(색상/마이너틱) + y라벨 좌표 정렬
    style_axis_colors(ax3, ax4, cop_color, X_eff_color)
    align_ylabel_positions(ax3, ax4)

    # y축 폰트/간격
    ax3.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax4.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax3.spines['left'].set_linewidth(0.6)
    ax4.spines['right'].set_linewidth(0.6) 

    ax3.set_xlabel('Day of month [day]', fontsize=fs['label'])
    
# 그리기 루프
for r in range(2):
    for c in range(2):
        month = layout[r][c]
        mdf = df_sub[df_sub['Month'] == month].sort_values('xpos')

        # 월 내부 상·하 그래프 간격은 여기서 조정 (hspace)
        inner = gridspec.GridSpecFromSubplotSpec(2, 1, subplot_spec=outer[r, c], hspace=0.18)
        ax_top = fig.add_subplot(inner[0, 0])                 # 상단(외기온+부하)
        ax_bot = fig.add_subplot(inner[1, 0], sharex=ax_top)  # 하단(COP+엑서지)

        plot_one_month(ax_top, ax_bot, mdf, month, start_map)

# plt.savefig('figure/Fig. 12.png', dpi=600)
# plt.savefig('figure/Fig. 12.pdf', dpi=600)
dm.util.save_and_show(fig)

## Fig. 13 월별 환경온도 + 엑서지 input, consumption, output

In [40]:
# Wh 단위를 GWH 단위로 변환 변수
Wh2GWh = 1 / 1000000000

# 월별 데이터를 그룹화하기 위해 'Month' 열 생성
weekday_df['Month'] = weekday_df['Date/Time_clean'].str.split('/').str[0].astype(int)

# 월별 그룹화
grouped = weekday_df.groupby('Month')

# 월별 리스트 생성
monthly_exergy_input = []
monthly_exergy_consumption = []
monthly_exergy_output = []
monthly_avg_COP = []
monthly_exergy_efficiency = []

# 월별 온도 리스트 생성
monthly_avg_temp = grouped['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)'].mean().tolist()
monthly_min_temp = grouped['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)'].min().tolist()
monthly_max_temp = grouped['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)'].max().tolist()

for month, group in grouped:
    input_exergy = 0
    consumption_exergy = 0
    output_exergy = 0
    
    total_cooling_exergy_efficiency = 0
    total_heating_exergy_efficiency = 0
    total_cooling_COP = 0
    total_heating_COP = 0
    cooling_count = 0
    heating_count = 0

    for _, row in group.iterrows():
        Toa = row['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)']
        Tia = row['CORE_ZN:Zone Air Temperature [C](TimeStep)']
        cooling_load = row['DistrictCooling:Facility [J](TimeStep)'] / 3600
        heating_load = row['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600

        if cooling_load > 0:
            ASHP_cooling = enex.AirSourceHeatPump_cooling()
            ASHP_cooling.T0 = Toa
            ASHP_cooling.T_a_room = 22
            ASHP_cooling.Q_r_int = cooling_load
            ASHP_cooling.Q_r_max = max(cooling_load_list)
            ASHP_cooling.system_update()
            if ASHP_cooling.X_eff > 0:
                input_exergy += (ASHP_cooling.E_cmp + ASHP_cooling.E_fan_int + ASHP_cooling.E_fan_ext) * 3600
                output_exergy += (ASHP_cooling.X_a_int_out - ASHP_cooling.X_a_int_in) * 3600
                total_cooling_COP += ASHP_cooling.COP_sys
                total_cooling_exergy_efficiency += ASHP_cooling.X_eff
                cooling_count += 1
            else:
                cooling_count += 0
        else:
            cooling_count += 0
            
        if heating_load > 0:
            ASHP_heating = enex.AirSourceHeatPump_heating()
            ASHP_heating.T0 = Toa
            ASHP_heating.T_a_room = 22
            ASHP_heating.Q_r_int = heating_load
            ASHP_heating.Q_r_max = max(heating_load_list)
            ASHP_heating.system_update()
            if ASHP_heating.X_eff > 0:
                input_exergy += (ASHP_heating.E_cmp + ASHP_heating.E_fan_int + ASHP_heating.E_fan_ext) * 3600
                output_exergy += (ASHP_heating.X_a_int_out - ASHP_heating.X_a_int_in) * 3600
                total_heating_COP += ASHP_heating.COP_sys
                total_heating_exergy_efficiency += ASHP_heating.X_eff
                heating_count += 1
            else:
                heating_count += 0
        else:
            heating_count += 0

    consumption_exergy = input_exergy - output_exergy

    monthly_exergy_input.append(input_exergy * Wh2GWh)
    monthly_exergy_consumption.append(consumption_exergy * Wh2GWh)
    monthly_exergy_output.append(output_exergy * Wh2GWh)

    avg_exergy_efficiency = (total_cooling_exergy_efficiency + total_heating_exergy_efficiency) / (cooling_count + heating_count) if (cooling_count + heating_count) > 0 else None
    monthly_exergy_efficiency.append(avg_exergy_efficiency * 100 if avg_exergy_efficiency is not None else 0)
    avg_COP = (total_cooling_COP + total_heating_COP) / (cooling_count + heating_count) if (cooling_count + heating_count) > 0 else None
    monthly_avg_COP.append(avg_COP)

In [20]:
labels = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
x = np.arange(1, 13)

# Create figure with 2 subplots vertically stacked
fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(dm.cm2in(17), dm.cm2in(11)), gridspec_kw={'height_ratios': [1.0, 1.4]})
plt.subplots_adjust(left=0.08, right=0.92, top=0.95, bottom=0.08, wspace=0.2, hspace=0.2)

# Colors
fill_color = 'dm.gray1'
min_temp_color = 'dm.blue5'
max_temp_color = 'dm.red5'
avg_temp_color = 'dm.gray8'
percentage_color = 'dm.black'
avg_cop_color = 'dm.orange6'

# Common setting
marker_size = 1.5
line_width = 0.5

# --- FIRST SUBPLOT: TEMPERATURE ---
ax1.fill_between(x, monthly_min_temp, monthly_max_temp, color=fill_color, alpha=0.6)

# ax1 plot
ax1.plot(x, monthly_max_temp, color=max_temp_color, linewidth=line_width, label='Max', marker='o', markersize=marker_size)
ax1.plot(x, monthly_avg_temp, color=avg_temp_color, linewidth=line_width, label='Avg', marker='o', markersize=marker_size)
ax1.plot(x, monthly_min_temp, color=min_temp_color, linewidth=line_width, label='Min', marker='o', markersize=marker_size)

# Limit
ax1.set_xlim(0.5, 12.5)
ax1.set_ylim(-10, 40)

# Tick
ax1.set_xticks(x)
ax1.set_xticklabels(labels, fontsize=fs['tick'])
ax1.set_yticks(np.arange(-10, 41, 10))
ax1.set_yticklabels(np.arange(-10, 41, 10), fontsize=fs['tick'])
ax1.tick_params(axis='both', which='major', labelsize=fs['tick'])
ax1.tick_params(axis='x', which='minor', bottom=False)
ax1.text(0.01, 0.97, '(a)', transform=ax1.transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# Axis and title
ax1.set_ylabel('Environmental temperature [$^{\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
ax1.grid(True, linestyle='--', alpha=0.5)
ax1.legend(
    loc='upper right', ncol=3, frameon=False,
    fontsize=fs['legend'], fancybox=False,
    columnspacing=1.00, labelspacing=0.8,
    bbox_to_anchor=(0.99, 1.01),
    handlelength=1.8
)

ax1.axhline(y=22, color='dm.teal6', linestyle='--', linewidth=line_width, label='Setpoint')
ax1.text(0.6, 24, 'Setpoint', rotation=0, fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='center')

# --- SECOND SUBPLOT: EXERGY STACKED BAR ---
# Exergy input
total_exergy = np.array(monthly_exergy_input)

# Common settings
bar_width = 0.57
spine_width = 0.5

# Colors
colors = ['dm.gray2', 'dm.green3', 'dm.orange7']
edge_color = 'dm.gray8'

# Stacked bar plot
bar_top = ax2.bar(x, monthly_exergy_consumption, bar_width, bottom=monthly_exergy_output, 
                 label='Exergy consumption', color=colors[0], alpha=1.0, zorder=3)
bar_bottom = ax2.bar(x, monthly_exergy_output, bar_width, 
                    label='Exergy output', color=colors[1], alpha=0.75, zorder=3)

# Add percentage labels
for i in range(len(labels)):
    x_pos = x[i]
    consumption = monthly_exergy_consumption[i]
    output = monthly_exergy_output[i]
    consumption_ratio = consumption * 100 / total_exergy[i]
    output_ratio = output * 100 / total_exergy[i]
    ax2.text(
        x_pos, output + consumption / 2,
        f'{consumption_ratio:.1f}%',
        ha='center', va='center',
        fontsize=fs['text'], color=percentage_color, zorder=4)
    ax2.text(
        x_pos, output / 2,
        f'{output_ratio:.1f}%',
        ha='center', va='center',
        fontsize=fs['text'], color=percentage_color, zorder=4)
    
# Add rectangle outlines
for i in range(len(labels)):
    total_height = monthly_exergy_consumption[i] + monthly_exergy_output[i]
    rect = plt.Rectangle(
        (x[i] - bar_width / 2, 0),
        bar_width,
        total_height,
        linewidth=line_width,
        edgecolor=edge_color,
        facecolor='none',
        alpha=0.7, zorder=3
    )
    ax2.add_patch(rect)

# Create custom legend element
from matplotlib.patches import Patch
input_legend = Patch(
    facecolor='none', edgecolor=edge_color,
    linewidth=line_width, alpha=0.7,
    label='Exergy input'
)

# Label
ax2.set_ylabel('Exergy [GWh]', fontsize=fs['label'], labelpad=pad['label'] + 5)

# Limit
ax2.set_xlim(0.5, 12.5)
ax2.set_ylim(0, 5)

# Tick
ax2.set_xticks(x)
ax2.set_xticklabels(labels, fontsize=fs['tick'])
ax2.set_ylim(0.0, 5.0)
ax2.set_yticklabels(np.arange(0, 6, 1), fontsize=fs['tick'])
ax2.tick_params(axis='both', which='major', labelsize=fs['tick'])
ax2.tick_params(axis='x', which='major', bottom=False)
ax2.tick_params(axis='x', which='minor', bottom=False)
ax2.text(0.01, 0.97, '(b)', transform=ax2.transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')
ax2.spines['right'].set_visible(False)

# Add secondary y-axis for monthly_avg_COP
ax2_right = ax2.twinx()
ax2_right.plot(x, monthly_avg_COP, color=avg_cop_color, linewidth=line_width, label='COP', marker='o', markersize=marker_size)
ax2_right.set_ylabel('Average COP$_{sys}$ [ - ]', fontsize=fs['label'], labelpad=pad['label'] + 5, color=avg_cop_color)
ax2_right.set_ylim(0.0, 5.0)
ax2_right.set_yticks(np.arange(0.0, 5.1, 1.0))
ax2_right.tick_params(axis='y', labelsize=fs['tick'], color=avg_cop_color, labelcolor=avg_cop_color)
ax2_right.tick_params(axis='y', which='minor', color=avg_cop_color)
ax2_right.spines['right'].set_color(avg_cop_color)
ax2_right.spines['right'].set_linewidth(spine_width)

# Grid
ax2.grid(True, linestyle='--', alpha=0.6, zorder=1)
ax2.xaxis.grid(False)

# Legend (combined for ax2 and ax2_right, 4 columns)
handles_left, labels_left = ax2.get_legend_handles_labels()
handles_left.insert(0, input_legend)
labels_left.insert(0, 'Exergy input')

handles_right, labels_right = ax2_right.get_legend_handles_labels()

# Combine handles and labels
handles_combined = handles_left + handles_right
labels_combined = labels_left + labels_right

legend = ax2.legend(
    handles_combined, labels_combined,
    loc='upper right', ncol=4, frameon=False,
    fontsize=fs['legend'], fancybox=False,
    columnspacing=1.0, labelspacing=1.0,
    bbox_to_anchor=(0.99, 1.01),
    handlelength=1.8
)

# plt.savefig('figure/Fig. 13.png', dpi=600)
plt.savefig('figure/Fig. 13.svg', dpi=600, transparent=True)
dm.util.save_and_show(fig)

## Fig X. PLR 격자 형태

In [25]:
ASHP_cooling_exergy_effi = []
ASHP_heating_exergy_effi = []
ASHP_cooling_PLR = []
ASHP_heating_PLR = []
ASHP_cooling_ex_load_eff = []
ASHP_heating_ex_load_eff = []
ASHP_cooling_COP = []
ASHP_heating_COP = []
dV_int_cooling_list = []
dV_ext_cooling_list = []
dV_int_heating_list = []
dV_ext_heating_list = []

for Toa, cooling_load, heating_load in zip(Toa_list, cooling_load_list, heating_load_list):
    # 냉방 엑서지 효율 계산
    if cooling_load > 0:
        ASHP_cooling = enex.AirSourceHeatPump_cooling()
        ASHP_cooling.T0 = Toa
        ASHP_cooling.T_a_room = 22
        ASHP_cooling.Q_r_int = cooling_load
        ASHP_cooling.Q_r_max = max(cooling_load_list)
        ASHP_cooling.system_update()
        if ASHP_cooling.X_eff < 0:
            ASHP_cooling_exergy_effi.append(None)
            ASHP_cooling_COP.append(None)
        else:          
            ASHP_cooling_exergy_effi.append(ASHP_cooling.X_eff)
            ASHP_cooling_PLR.append(ASHP_cooling.Q_r_int / ASHP_cooling.Q_r_max)
            ASHP_cooling_ex_load_eff.append(1-enex.C2K(Toa)/enex.C2K(ASHP_cooling.T_a_room))
            ASHP_cooling_COP.append(ASHP_cooling.COP_sys)
            dV_int_cooling_list.append(ASHP_cooling.dV_int)
            dV_ext_cooling_list.append(ASHP_cooling.dV_ext)
    else:
        ASHP_cooling_exergy_effi.append(None)
        ASHP_cooling_COP.append(None)

    # 난방 엑서지 효율 계산
    if heating_load > 0:
        ASHP_heating = enex.AirSourceHeatPump_heating()
        ASHP_heating.T0 = Toa
        ASHP_heating.T_a_room = 22
        ASHP_heating.Q_r_int = heating_load
        ASHP_heating.Q_r_max = max(heating_load_list)
        ASHP_heating.system_update() 
        if ASHP_heating.X_eff < 0:
            ASHP_heating_exergy_effi.append(None)
            ASHP_heating_COP.append(None)
        else:
            ASHP_heating_exergy_effi.append(ASHP_heating.X_eff)
            ASHP_heating_PLR.append(ASHP_heating.Q_r_int / ASHP_heating.Q_r_max)
            ASHP_heating_ex_load_eff.append(1-enex.C2K(Toa)/enex.C2K(ASHP_heating.T_a_room))
            ASHP_heating_COP.append(ASHP_heating.COP_sys)
            dV_int_heating_list.append(ASHP_heating.dV_int)
            dV_ext_heating_list.append(ASHP_heating.dV_ext)
    else:
        ASHP_heating_exergy_effi.append(None)
        ASHP_heating_COP.append(None)

# None 값 제거 함수    
def remove_none(lst):
    return [x for x in lst if x is not None]

ASHP_cooling_COP_filtered = remove_none(ASHP_cooling_COP)
ASHP_heating_COP_filtered = remove_none(ASHP_heating_COP)
ASHP_cooling_exergy_effi_filtered = remove_none(ASHP_cooling_exergy_effi)
ASHP_heating_exergy_effi_filtered = remove_none(ASHP_heating_exergy_effi)

# 엑서지효율 None 값일 때 해당하는 온도, 부하를 제거한 필터링된 리스트
Date_cooling_list_filtered = [date for date, eff in zip(date_list, ASHP_cooling_exergy_effi) if eff is not None]
Date_heating_list_filtered = [date for date, eff in zip(date_list, ASHP_heating_exergy_effi) if eff is not None]
Tia_cooling_list_filtered = [Tia for Tia, eff in zip(Tia_list, ASHP_cooling_exergy_effi) if eff is not None]
Tia_heating_list_filtered = [Tia for Tia, eff in zip(Tia_list, ASHP_heating_exergy_effi) if eff is not None]
Toa_cooling_list_filtered = [Toa for Toa, eff in zip(Toa_list, ASHP_cooling_exergy_effi) if eff is not None]
Toa_heating_list_filtered = [Toa for Toa, eff in zip(Toa_list, ASHP_heating_exergy_effi) if eff is not None]
cooling_load_list_filtered = [load for load, eff in zip(cooling_load_list, ASHP_cooling_exergy_effi) if eff is not None]
heating_load_list_filtered = [load for load, eff in zip(heating_load_list, ASHP_heating_exergy_effi) if eff is not None]

len(ASHP_cooling_COP_filtered), len(ASHP_heating_COP_filtered), len(Date_cooling_list_filtered), len(Date_heating_list_filtered), len(Tia_cooling_list_filtered), len(Tia_heating_list_filtered), len(Toa_cooling_list_filtered), len(Toa_heating_list_filtered), len(cooling_load_list_filtered), len(heating_load_list_filtered)

(1693, 1701, 1693, 1701, 1693, 1701, 1693, 1701, 1693, 1701)

In [26]:
cmax1, cmin1, cint1 = 100, 0, 20
cmax2, cmin2, cint2 = 100, 0, 20

# 텍스트 컬러 임계값 (격자 내 숫자 색상 결정)
cooling_plr_white_text = 65   # [%] 이상이면 흰색, 미만이면 검은색
heating_plr_white_text = 65   # [%] 이상이면 흰색, 미만이면 검은색

# Data
# Cooling
Toa_c = np.array(Toa_cooling_list_filtered)
Load_c = np.array(cooling_load_list_filtered) / 1000 
PLR_c = np.array(ASHP_cooling_PLR) * 100  # [%]로 변환

# Heating
Toa_h = np.array(Toa_heating_list_filtered)
Load_h = np.array(heating_load_list_filtered) / 1000
PLR_h = np.array(ASHP_heating_PLR) * 100  # [%]로 변환

# Bins
bins_x = np.arange(x_range[0], x_range[1]+bin_temp, bin_temp)
bins_y = np.arange(y_range[0], y_range[1]+bin_load, bin_load)

# Calculate average PLR(엑서지 효율) in each grid
avg_c, xedges, yedges = grid_stats(Toa_c, Load_c, PLR_c, bins_x, bins_y)
avg_h, _, _ = grid_stats(Toa_h, Load_h, PLR_h, bins_x, bins_y)

# Plot
fig, axes = plt.subplots(2, 1, figsize=(dm.cm2in(17), dm.cm2in(13)), sharex=False, sharey=True)
plt.subplots_adjust(left=0.07, right=1.07, top=0.95, bottom=0.08, hspace=0.25)  

# Cooling plot
im1 = axes[0].pcolormesh(xedges, yedges, avg_c, cmap=coolwarm_left.reversed(), vmin=cmin1, vmax=cmax1)
for i in range(len(xedges)-1):
    for j in range(len(yedges)-1):
        rect = plt.Rectangle(
            (xedges[i], yedges[j]),
            xedges[i+1] - xedges[i],
            yedges[j+1] - yedges[j],
            linewidth=line_width,
            edgecolor='white',
            facecolor='none',
            zorder=1
        )
        axes[0].add_patch(rect)
        if not np.isnan(avg_c[j,i]):
            # 값에 따라 텍스트 색상 결정 (COP 코드와 동일한 로직)
            text_color = 'white' if avg_c[j,i] >= cooling_plr_white_text else 'black'
            axes[0].text((xedges[i]+xedges[i+1])/2, (yedges[j]+yedges[j+1])/2,
                         f"{avg_c[j,i]:.1f}",
                         ha='center', va='center', fontsize=fs['text'], color=text_color)
axes[0].set_ylabel('Cooling load [kW]', fontsize=fs['label'], labelpad=pad['label'])
axes[0].minorticks_off()
cbar1 = fig.colorbar(im1, ax=axes[0], label='Part load ratio [%]', orientation='vertical', pad=0.02, aspect=20)
cbar1.set_label('Part load ratio [%]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar1.set_ticks(np.arange(cmin1, cmax1+1, cint1))
cbar1.ax.tick_params(axis='both', which='major', labelsize=fs['cbar_tick'])
cbar1.ax.tick_params(axis='both', which='minor', bottom=False, left=False)
cbar1.ax.minorticks_off()
axes[0].axvline(x=22, color='dm.teal6', linestyle='--', linewidth=0.6, label='Setpoint')
axes[0].text(20.8, 26.2, 'Setpoint', rotation=90, fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='center')
axes[0].text(0.01, 0.97, '(a)', transform=axes[0].transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# Heating plot
im2 = axes[1].pcolormesh(xedges, yedges, avg_h, cmap=coolwarm_right, vmin=cmin2, vmax=cmax2)
for i in range(len(xedges)-1):
    for j in range(len(yedges)-1):
        rect = plt.Rectangle(
            (xedges[i], yedges[j]),
            xedges[i+1] - xedges[i],
            yedges[j+1] - yedges[j],
            linewidth=line_width,
            edgecolor='dm.white',
            facecolor='none',
            zorder=1
        )
        axes[1].add_patch(rect)
        if not np.isnan(avg_h[j,i]):
            # 값에 따라 텍스트 색상 결정 (COP 코드와 동일한 로직)
            text_color = 'white' if avg_h[j,i] >= heating_plr_white_text else 'black'
            axes[1].text((xedges[i]+xedges[i+1])/2, (yedges[j]+yedges[j+1])/2,
                         f"{avg_h[j,i]:.1f}",
                         ha='center', va='center', fontsize=fs['text'], color=text_color)
axes[1].set_ylabel('Heating load [kW]', fontsize=fs['label'], labelpad=pad['label'])
axes[1].minorticks_off()
cbar2 = fig.colorbar(im2, ax=axes[1], label='Part load ratio [%]', orientation='vertical', pad=0.02, aspect=20)
cbar2.set_label('Part load ratio [%]', fontsize=fs['cbar_label'], labelpad=pad['label'])
cbar2.set_ticks(np.arange(cmin2, cmax2+1, cint2))
cbar2.ax.tick_params(axis='both', which='major', labelsize=fs['cbar_tick'])
cbar2.ax.tick_params(axis='both', which='minor', bottom=False, left=False)
cbar2.ax.minorticks_off()
axes[1].axvline(x=22, color='dm.teal6', linestyle='--', linewidth=0.6, label='Setpoint')
axes[1].text(20.8, 26.2, 'Setpoint', rotation=90, fontsize=fs['setpoint'], color='dm.teal6', ha='left', va='center')
axes[1].text(0.01, 0.97, '(b)', transform=axes[1].transAxes, fontsize=fs['subtitle'], fontweight='bold', va='top', ha='left')

# Common settings
for ax in axes:
    ax.set_xlim(x_range)
    ax.set_ylim(y_range)
    ax.set_xlabel('Environmental temperature [$^{\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
    ax.grid(True, linestyle='--', alpha=0.5)
    ax.set_xticks(xedges, minor=True)
    ax.tick_params(axis='x', which='minor', length=1.6, color='dm.gray7')

# plt.savefig('figure/Fig. 11.png', dpi=600)
# plt.savefig('figure/Fig. 11.pdf', dpi=600)
dm.util.save_and_show(fig)

## Fig. X Energy efficiency

In [13]:
# cooling COP 최대일 때의 날짜, 환경온도, 실내온도, 냉방부하
max_cooling_COP_index = ASHP_cooling_COP_filtered.index(max(ASHP_cooling_COP_filtered))
print("Cooling COP Maximum Details: =======================================")
print("Maximum Cooling COP:", max(ASHP_cooling_COP_filtered))
print("Date:", Date_cooling_list_filtered[max_cooling_COP_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_cooling_list_filtered[max_cooling_COP_index]))
print("Indoor Temperature (Tia): {:.1f}".format(Tia_cooling_list_filtered[max_cooling_COP_index]))
print("Cooling Load: {:.1f}".format(cooling_load_list_filtered[max_cooling_COP_index]))
print()

# cooling COP 최소일 때의 날짜, 환경온도, 실내온도, 냉방부하
min_cooling_COP_index = ASHP_cooling_COP_filtered.index(min(ASHP_cooling_COP_filtered))
print("Cooling COP Minimum Details: ======================================")
print("Minimum Cooling COP:", min(ASHP_cooling_COP_filtered))
print("Date:", Date_cooling_list_filtered[min_cooling_COP_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_cooling_list_filtered[min_cooling_COP_index]))
print("Indoor Temperature (Tia): {:.1f}".format(Tia_cooling_list_filtered[min_cooling_COP_index]))
print("Cooling Load: {:.1f}".format(cooling_load_list_filtered[min_cooling_COP_index]))
print()

# heating COP 최대일 때의 날짜, 환경온도, 실내온도, 난방부하
max_heating_COP_index = ASHP_heating_COP_filtered.index(max(ASHP_heating_COP_filtered))
print("Heating COP Maximum Details: =======================================")
print("Maximum Heating COP:", max(ASHP_heating_COP_filtered))
print("Date:", Date_heating_list_filtered[max_heating_COP_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_heating_list_filtered[max_heating_COP_index]))
print("Indoor Temperature (Tia): {:.1f}".format(Tia_heating_list_filtered[max_heating_COP_index]))
print("Heating Load: {:.1f}".format(heating_load_list_filtered[max_heating_COP_index]))
print()

# heating COP 최소일 때의 날짜, 환경온도, 실내온도, 난방부하
min_heating_COP_index = ASHP_heating_COP_filtered.index(min(ASHP_heating_COP_filtered))
print("Heating COP Minimum Details: =======================================")
print("Minimum Heating COP:", min(ASHP_heating_COP_filtered))
print("Date:", Date_heating_list_filtered[min_heating_COP_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_heating_list_filtered[min_heating_COP_index]))
print("Indoor Temperature (Tia): {:.1f}".format(Tia_heating_list_filtered[min_heating_COP_index]))
print("Heating Load: {:.1f}".format(heating_load_list_filtered[min_heating_COP_index]))

Cooling COP Maximum Details: =======================================
Maximum Cooling COP: 4.246424858705447
Date: 09/05 11:00:00
Outdoor Temperature (Toa): 23.5
Indoor Temperature (Tia): 22.0
Cooling Load: 15173.0

Cooling COP Minimum Details: ======================================
Minimum Cooling COP: 2.4413010381499114
Date: 08/14 06:00:00
Outdoor Temperature (Toa): 26.0
Indoor Temperature (Tia): 22.0
Cooling Load: 1878.8

Heating COP Maximum Details: =======================================
Maximum Heating COP: 4.33086088152948
Date: 11/24 08:00:00
Outdoor Temperature (Toa): 8.4
Indoor Temperature (Tia): 22.0
Heating Load: 13700.0

Heating COP Minimum Details: =======================================
Minimum Heating COP: 0.7499843880062533
Date: 01/13 07:00:00
Outdoor Temperature (Toa): -7.0
Indoor Temperature (Tia): 22.0
Heating Load: 20233.7


In [250]:
# coolwarm 컬러맵의 왼쪽 절반만 사용
coolwarm_left = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_left', get_cmap('coolwarm')(np.linspace(0, 0.45, 256))
)

# coolwarm 컬러맵의 오른쪽 절반만 사용
coolwarm_right = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_right', get_cmap('coolwarm')(np.linspace(0.55, 1.0, 256))
)

# Set up the plot
fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(dm.cm2in(17), dm.cm2in(8)))
plt.subplots_adjust(left=0.07, right=0.93, top=0.9, bottom=0.15, wspace=0.1, hspace=0.1)

# 메인 축을 기준으로 divider 생성
divider = make_axes_locatable(ax)

# Common setting
label_pad = 8
line_width = 0.6

# Normalize for colorbar
norm_cooling = mcolors.Normalize(vmin=2, vmax=4.5)
norm_heating = mcolors.Normalize(vmin=2, vmax=4.5)

# Scatter plot
cax1 = divider.append_axes("right", size="3%", pad=0.2)
sc1 = ax.scatter(Toa_cooling_list_filtered, 
                 [load / 1000 for load in cooling_load_list_filtered], 
                 c=[eff for eff in ASHP_cooling_COP_filtered],
                 cmap=coolwarm_left.reversed(), 
                 s=2.5, alpha=1.0, norm=norm_cooling,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar1 = fig.colorbar(sc1, cax=cax1)
cbar1.set_ticks(np.arange(2, 4.6, 0.5))
cbar1.ax.tick_params(labelsize=cbar_fontsize)
cbar1.ax.text(0.5, 1.03, 'Cooling', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar1.ax.transAxes)
cbar1.ax.minorticks_off()

cax2 = divider.append_axes("right", size="3%", pad=0.4)
sc2 = ax.scatter(Toa_heating_list_filtered, 
                 [load / 1000 for load in heating_load_list_filtered], 
                 c=[eff for eff in ASHP_heating_COP_filtered], 
                 cmap=coolwarm_right, 
                 s=2.5, alpha=1.0, norm=norm_heating,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar2 = fig.colorbar(sc2, cax=cax2)
cbar2.set_ticks(np.arange(2, 4.6, 0.5))
cbar2.ax.tick_params(labelsize=cbar_fontsize)
cbar2.set_label('Energy efficiency (COP$_{sys}$) [ - ]', fontsize=cbar_fontsize, labelpad=label_pad+2)
cbar2.ax.text(0.5, 1.03, 'Heating', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar2.ax.transAxes)
cbar2.ax.minorticks_off()

ax.axvline(x=22, color='dm.teal6', linestyle='--', linewidth=line_width, label='Setpoint temperature')
ax.text(20.5, 23, 'Setpoint temperature', rotation=90, fontsize=setpoint_fontsize, color='dm.teal6', ha='left', va='center')

# limit
ax.set_xlim(-10, 35)
ax.set_ylim(0, 30)

# label
ax.set_xlabel('Environmental temperature [$^{\circ}$C]', fontsize=label_fontsize)
ax.set_ylabel('Load [kW]', fontsize=label_fontsize, labelpad=label_pad)

# Tick
ax.set_xticks(np.arange(-10, 36, 5))
ax.set_yticks(np.linspace(0, 30, 7))
ax.tick_params(axis='both', which='major', labelsize=tick_fontsize)
ax.tick_params(axis='both', which='minor', labelsize=tick_fontsize)

ax.grid(True)

plt.savefig('figure/Fig. 8.png', dpi=600)
dm.util.save_and_show(fig)

## Fig. X Exergy efficiency

In [57]:
# cooling exergy efficiency 최대일 때의 날짜, 환경온도, 실내온도, 냉방부하
max_cooling_exergy_index = ASHP_cooling_exergy_effi_filtered.index(max(ASHP_cooling_exergy_effi_filtered))
print("Cooling Exergy Efficiency Maximum Details: =======================================")
print("Maximum Cooling Exergy Efficiency: {:.1f}".format(max(ASHP_cooling_exergy_effi_filtered) * 100))
print("Date:", Date_cooling_list_filtered[max_cooling_exergy_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_cooling_list_filtered[max_cooling_exergy_index]))
# print("Indoor Temperature (Tia): {:.1f}".format(Tia_cooling_list_filtered[max_cooling_exergy_index]))
print("Cooling Load: {:.1f}".format(cooling_load_list_filtered[max_cooling_exergy_index]))
print()

# cooling exergy efficiency 최소일 때의 날짜, 환경온도, 실내온도, 냉방부하
min_cooling_exergy_index = ASHP_cooling_exergy_effi_filtered.index(min(ASHP_cooling_exergy_effi_filtered))
print("Cooling Exergy Efficiency Minimum Details: ======================================")
print("Minimum Cooling Exergy Efficiency: {:.1f}".format(min(ASHP_cooling_exergy_effi_filtered) * 100))
print("Date:", Date_cooling_list_filtered[min_cooling_exergy_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_cooling_list_filtered[min_cooling_exergy_index]))
# print("Indoor Temperature (Tia): {:.1f}".format(Tia_cooling_list_filtered[min_cooling_exergy_index]))
print("Cooling Load: {:.1f}".format(cooling_load_list_filtered[min_cooling_exergy_index]))
print()

# heating exergy efficiency 최대일 때의 날짜, 환경온도, 실내온도, 난방부하
max_heating_exergy_index = ASHP_heating_exergy_effi_filtered.index(max(ASHP_heating_exergy_effi_filtered))
print("Heating Exergy Efficiency Maximum Details: =======================================")
print("Maximum Heating Exergy Efficiency: {:.1f}".format(max(ASHP_heating_exergy_effi_filtered) * 100))
print("Date:", Date_heating_list_filtered[max_heating_exergy_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_heating_list_filtered[max_heating_exergy_index]))
# print("Indoor Temperature (Tia): {:.1f}".format(Tia_heating_list_filtered[max_heating_exergy_index]))
print("Heating Load: {:.1f}".format(heating_load_list_filtered[max_heating_exergy_index]))
print()

# heating exergy efficiency 최소일 때의 날짜, 환경온도, 실내온도, 난방부하
min_heating_exergy_index = ASHP_heating_exergy_effi_filtered.index(min(ASHP_heating_exergy_effi_filtered))
print("Heating Exergy Efficiency Minimum Details: =======================================")
print("Minimum Heating Exergy Efficiency: {:.1f}".format(min(ASHP_heating_exergy_effi_filtered) * 100))
print("Date:", Date_heating_list_filtered[min_heating_exergy_index])
print("Outdoor Temperature (Toa): {:.1f}".format(Toa_heating_list_filtered[min_heating_exergy_index]))
# print("Indoor Temperature (Tia): {:.1f}".format(Tia_heating_list_filtered[min_heating_exergy_index]))
print("Heating Load: {:.1f}".format(heating_load_list_filtered[min_heating_exergy_index]))

Cooling Exergy Efficiency Maximum Details: =======================================
Maximum Cooling Exergy Efficiency: 20.2
Date: 08/09 15:00:00
Outdoor Temperature (Toa): 33.8
Cooling Load: 23238.3

Cooling Exergy Efficiency Minimum Details: ======================================
Minimum Cooling Exergy Efficiency: 0.0
Date: 09/28 21:00:00
Outdoor Temperature (Toa): 16.0
Cooling Load: 520.3

Heating Exergy Efficiency Maximum Details: =======================================
Maximum Heating Exergy Efficiency: 30.6
Date: 12/27 10:00:00
Outdoor Temperature (Toa): -3.0
Heating Load: 13257.6

Heating Exergy Efficiency Minimum Details: =======================================
Minimum Heating Exergy Efficiency: 6.1
Date: 10/23 19:00:00
Outdoor Temperature (Toa): 21.0
Heating Load: 16.1


In [251]:
# coolwarm 컬러맵의 왼쪽 절반만 사용
coolwarm_left = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_left', get_cmap('coolwarm')(np.linspace(0, 0.45, 256))
)

# coolwarm 컬러맵의 오른쪽 절반만 사용
coolwarm_right = mcolors.LinearSegmentedColormap.from_list(
    'coolwarm_right', get_cmap('coolwarm')(np.linspace(0.55, 1.0, 256))
)

# Set up the plot
fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(dm.cm2in(17), dm.cm2in(8)))
plt.subplots_adjust(left=0.07, right=0.93, top=0.9, bottom=0.15, wspace=0.1, hspace=0.1)

# 메인 축을 기준으로 divider 생성
divider = make_axes_locatable(ax)

# Common setting
label_pad = 8
line_width = 0.6

# Normalize for colorbar
norm_cooling = mcolors.Normalize(vmin=0, vmax=20)
norm_heating = mcolors.Normalize(vmin=0, vmax=32)

# Scatter plot
cax1 = divider.append_axes("right", size="3%", pad=0.2)
sc1 = ax.scatter(Toa_cooling_list_filtered, 
                 [load / 1000 for load in cooling_load_list_filtered], 
                 c=[eff * 100 for eff in ASHP_cooling_exergy_effi_filtered],
                 cmap=coolwarm_left.reversed(), 
                 s=2.5, alpha=1.0, norm=norm_cooling,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar1 = fig.colorbar(sc1, cax=cax1)
cbar1.set_ticks(np.arange(0, 21, 5))
cbar1.ax.tick_params(labelsize=cbar_fontsize)
cbar1.ax.text(0.5, 1.03, 'Cooling', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar1.ax.transAxes)
cbar1.ax.minorticks_off()

cax2 = divider.append_axes("right", size="3%", pad=0.4)
sc2 = ax.scatter(Toa_heating_list_filtered, 
                 [load / 1000 for load in heating_load_list_filtered], 
                 c=[eff * 100 for eff in ASHP_heating_exergy_effi_filtered], 
                 cmap=coolwarm_right, 
                 s=2.5, alpha=1.0, norm=norm_heating,
                 facecolors='none', linewidths=line_width, edgecolors='none')
cbar2 = fig.colorbar(sc2, cax=cax2)
cbar2.set_ticks(np.arange(0, 33, 8))
cbar2.ax.tick_params(labelsize=cbar_fontsize)
cbar2.set_label('Exergy efficiency [%]', fontsize=cbar_fontsize, labelpad=label_pad+2)
cbar2.ax.text(0.5, 1.03, 'Heating', fontsize=cbar_title_fontsize, ha='center', va='bottom', transform=cbar2.ax.transAxes)
cbar2.ax.minorticks_off()

ax.axvline(x=22, color='dm.teal6', linestyle='--', linewidth=line_width, label='Setpoint temperature')
ax.text(20.5, 23, 'Setpoint temperature', rotation=90, fontsize=setpoint_fontsize, color='dm.teal6', ha='left', va='center')

# limit
ax.set_xlim(-10, 35)
ax.set_ylim(0, 30)

# label
ax.set_xlabel('Environmental temperature [$^{\circ}$C]', fontsize=label_fontsize)
ax.set_ylabel('Load [kW]', fontsize=label_fontsize, labelpad=label_pad)

# Tick
ax.set_xticks(np.arange(-10, 36, 5))
ax.set_yticks(np.linspace(0, 30, 7))
ax.tick_params(axis='both', which='major', labelsize=tick_fontsize)
ax.tick_params(axis='both', which='minor', labelsize=tick_fontsize)

ax.grid(True)

# plt.savefig('figure/Fig. 9.png', dpi=600)
dm.util.save_and_show(fig)

# 에너지 & 엑서지 효율 카운트

In [16]:
# COP 데이터 필터링
filtered_cooling_COP = [cop for cop in ASHP_cooling_COP_filtered if 0 <= cop <= 6]
filtered_heating_COP = [cop for cop in ASHP_heating_COP_filtered if 0 <= cop <= 6]

bins1 = np.arange(0, 6.1, 0.1)
bins2 = np.arange(0, 6.1, 0.1)

# set up the plot
fig, axes = plt.subplots(1, 2, figsize=(dm.cm2in(17), dm.cm2in(7)), sharey=None)
plt.subplots_adjust(left=0.07, right=0.97, top=0.9, bottom=0.15, wspace=0.15, hspace=0.4)

# histogram plot
axes[0].hist(filtered_cooling_COP, bins=bins1, alpha=0.5, color='#5787D7', edgecolor='#3B4CC0')
axes[1].hist(filtered_heating_COP, bins=bins2, alpha=0.5, color='#E87B68', edgecolor='#C6413D')

# Common setting
line_width = 0.4

# Limit
axes[0].set_xlim(-0.2, 6.2)
axes[0].set_ylim(0, 250)
axes[1].set_xlim(-0.2, 6.2)
axes[1].set_ylim(0, 250)

# Label
axes[0].set_xlabel('COP$_{sys}$ [ - ]', fontsize=fs['label'], labelpad=pad['label'])
axes[0].set_ylabel('Count', fontsize=fs['label'], labelpad=pad['label'])
axes[1].set_xlabel('COP$_{sys}$ [ - ]', fontsize=fs['label'], labelpad=pad['label'])

# Tick
axes[0].set_xticks(np.arange(0, 6.5, 1))
axes[0].set_yticks(np.arange(0, 401, 100))
axes[0].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[0].tick_params(axis='both', which='minor', labelsize=fs['tick'])
axes[1].set_xticks(np.arange(0, 6.5, 1))
axes[1].set_yticks(np.arange(0, 401, 100))
axes[1].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[1].tick_params(axis='both', which='minor', labelsize=fs['tick'])

# Grid
axes[0].grid(True, which='major', linestyle='--', linewidth=0.1, alpha=0.7)
axes[1].grid(True, which='major', linestyle='--', linewidth=0.1, alpha=0.7)

# subtitle
axes[0].text(0.01, 1.09, '(a) Cooling mode', transform=axes[0].transAxes, fontsize=fs['subtitle'], va='top', ha='left')
axes[1].text(0.01, 1.09, '(b) Heating mode', transform=axes[1].transAxes, fontsize=fs['subtitle'], va='top', ha='left')

# plt.savefig('figure/cop_count.png', dpi=600)
dm.util.save_and_show(fig)

In [17]:
# 엑서지 효율 데이터 필터링
filtered_cooling_exergy_efficiency = [eff * 100 for eff in ASHP_cooling_exergy_effi_filtered if 0 <= eff * 100 <= 40]
filtered_heating_exergy_efficiency = [eff * 100 for eff in ASHP_heating_exergy_effi_filtered if 0 <= eff * 100 <= 40]

bins1 = np.arange(0, 41, 1)
bins2 = np.arange(0, 41, 1)

# set up the plot
fig, axes = plt.subplots(1, 2, figsize=(dm.cm2in(17), dm.cm2in(7)), sharey=None)
plt.subplots_adjust(left=0.07, right=0.97, top=0.9, bottom=0.15, wspace=0.15, hspace=0.4)

# histogram plot
axes[0].hist(filtered_cooling_exergy_efficiency, bins=bins1, alpha=0.5, color='#5787D7', edgecolor='#3B4CC0') 
axes[1].hist(filtered_heating_exergy_efficiency, bins=bins2, alpha=0.5, color='#E87B68', edgecolor='#C6413D') 

# Common setting
line_width = 0.4

# Limit
axes[0].set_xlim(-2, 42)
axes[0].set_ylim(0, 250)
axes[1].set_xlim(-2, 42)
axes[1].set_ylim(0, 250)

# Label
axes[0].set_xlabel('Exergy Efficiency [%]', fontsize=fs['label'], labelpad=pad['label'])
axes[0].set_ylabel('Count', fontsize=fs['label'], labelpad=pad['label'])
axes[1].set_xlabel('Exergy Efficiency [%]', fontsize=fs['label'], labelpad=pad['label'])

# Tick
axes[0].set_xticks(np.arange(0, 42, 5))
axes[0].set_yticks(np.arange(0, 251, 50))
axes[0].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[0].tick_params(axis='both', which='minor', labelsize=fs['tick'])
axes[1].set_xticks(np.arange(0, 42, 5))
axes[1].set_yticks(np.arange(0, 251, 50)) 
axes[1].tick_params(axis='both', which='major', labelsize=fs['tick'])
axes[1].tick_params(axis='both', which='minor', labelsize=fs['tick'])

# Grid
axes[0].grid(True, which='major', linestyle='--', linewidth=0.1, alpha=0.7)
axes[1].grid(True, which='major', linestyle='--', linewidth=0.1, alpha=0.7)

# subtitle
axes[0].text(0.01, 1.09, '(a) Cooling mode', transform=axes[0].transAxes, fontsize=fs['subtitle'], va='top', ha='left')
axes[1].text(0.01, 1.09, '(b) Heating mode', transform=axes[1].transAxes, fontsize=fs['subtitle'], va='top', ha='left')

# plt.savefig('figure/exergy_efficiency_count.png', dpi=600)
dm.util.save_and_show(fig)

# 추가 분석

In [160]:
# 1) 사용할 월과 부분집합 만들기
months_to_plot = [1, 4, 8, 10]

day_all = weekday_df['Date/Time_clean'].str.slice(3, 5).astype(int)  # 'MM/DD ...' → DD
mask = weekday_df['Month'].isin(months_to_plot) & day_all.between(10, 16)  # 21일까지로 수정
df_sub = weekday_df.loc[mask].copy()

# 표시/축용 보조 열
df_sub['Day'] = day_all[mask].values
hour_sub = df_sub['Date/Time_clean'].str.slice(6, 8).astype(int)  # '... HH:MM:SS' → HH
df_sub['xpos'] = df_sub['Day'] + hour_sub / 24.0  # 15.00 ~ 21.958...

# 최대 부하(정규화용) 한 번만 계산
Q_r_max_cooling = (df_sub['DistrictCooling:Facility [J](TimeStep)'] / 3600.0).max()
Q_r_max_heating = (df_sub['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0).max()

# 2) COP / 엑서지 계산 (부분집합에만 수행)
def compute_metrics(row):
    Toa = row['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)']
    cooling_load = row['DistrictCooling:Facility [J](TimeStep)'] / 3600.0
    heating_load = row['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0

    exergy_effi = 0.0
    cop = 0.0

    if cooling_load > 0:
        ASHP = enex.AirSourceHeatPump_cooling()
        ASHP.T0 = Toa
        ASHP.T_a_room = 22
        ASHP.Q_r_int = cooling_load
        ASHP.Q_r_max = Q_r_max_cooling
        ASHP.system_update()
        if ASHP.X_eff > 0:
            exergy_effi = ASHP.X_eff * 100.0
            cop = ASHP.COP_sys

    elif heating_load > 0:
        ASHP = enex.AirSourceHeatPump_heating()
        ASHP.T0 = Toa
        ASHP.T_a_room = 22
        ASHP.Q_r_int = heating_load
        ASHP.Q_r_max = Q_r_max_heating
        ASHP.system_update()
        if ASHP.X_eff > 0:
            exergy_effi = ASHP.X_eff * 100.0
            cop = ASHP.COP_sys

    return pd.Series({'COP': cop, 'ExergyEff': exergy_effi})

df_sub[['COP', 'ExergyEff']] = df_sub.apply(compute_metrics, axis=1)

# 3) 플롯 (부분집합만 순회)
fig, axes = plt.subplots(len(months_to_plot), 2,
                         figsize=(dm.cm2in(17), dm.cm2in(20)), sharex=False)
plt.subplots_adjust(left=0.08, right=0.92, top=0.97, bottom=0.05, hspace=0.35, wspace=0.4)

for i, month in enumerate(months_to_plot):
    mdf = df_sub[df_sub['Month'] == month].sort_values('xpos')

    # 왼쪽: 외기온도와 부하
    ax1 = axes[i, 0]
    ax2 = ax1.twinx()
    ax1.plot(mdf['xpos'], mdf['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)'], 
             label='Toa [°C]', color='blue', linewidth=0.8)
    if month in [1, 10]:  # 난방 부하만
        ax2.plot(mdf['xpos'], mdf['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0 / 1000, 
                 label='Heating Load [kW]', color='red', linewidth=0.8)
    elif month in [4, 8]:  # 냉방 부하만
        ax2.plot(mdf['xpos'], mdf['DistrictCooling:Facility [J](TimeStep)'] / 3600.0 / 1000, 
                 label='Cooling Load [kW]', color='orange', linewidth=0.8)

    ax1.set_xlim(10, 17)  # x축 범위
    ax1.set_ylabel('Environmental temperature [$^{\circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
    ax2.set_ylabel('Load [kW]', fontsize=fs['label'], labelpad=pad['label'])
    ax1.set_title(f'{month}', fontsize=fs['subtitle'])
    ax1.grid(True, linestyle='--', alpha=0.5)
    ax1.legend(loc='upper left', fontsize=fs['legend'])
    ax2.legend(loc='upper right', fontsize=fs['legend'])
    ax1.set_ylim(-10, 40)  # 외기온도 y축 범위
    ax1.set_yticks(np.arange(-10, 41, 10))
    ax2.set_ylim(0, 30)    # 부하 y축 범위
    ax2.set_yticks(np.arange(0, 31, 10))
    ax1.tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax2.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])

    # 오른쪽: COP와 엑서지 효율
    ax3 = axes[i, 1]
    ax4 = ax3.twinx()
    ax3.plot(mdf['xpos'], mdf['COP'], label='COP [ - ]', color='green', linewidth=0.8)
    ax4.plot(mdf['xpos'], mdf['ExergyEff'], label='Exergy Efficiency [%]', color='purple', linewidth=0.8)

    ax3.set_xlim(10, 17)  # x축 범위
    ax3.set_ylabel('Energy efficiency [ - ]', fontsize=fs['label'], labelpad=pad['label'])
    ax4.set_ylabel('Exergy efficiency [%]', fontsize=fs['label'], labelpad=pad['label'])
    ax3.set_title(f'{month}', fontsize=fs['subtitle'])
    ax3.grid(True, linestyle='--', alpha=0.5)
    ax3.legend(loc='upper left', fontsize=fs['legend'])
    ax4.legend(loc='upper right', fontsize=fs['legend'])
    ax3.set_ylim(0, 5)     # COP y축 범위
    ax4.set_ylim(0, 50)    # 엑서지 효율 y축 범위
    ax3.tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax4.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])

plt.savefig('figure/Fig. 14.png', dpi=600)
dm.util.save_and_show(fig)


In [288]:
ASHP_cooling_exergy_effi = []
ASHP_heating_exergy_effi = []
ASHP_cooling_COP = []
ASHP_heating_COP = []

for Toa, cooling_load, heating_load in zip(Toa_list, cooling_load_list, heating_load_list):
    # 냉방 엑서지 효율 계산
    if cooling_load > 0:
        ASHP_cooling = enex.AirSourceHeatPump_cooling()
        ASHP_cooling.T0 = Toa
        ASHP_cooling.T_a_room = 22
        ASHP_cooling.Q_r_int = cooling_load
        ASHP_cooling.Q_r_max = max(cooling_load_list)
        ASHP_cooling.system_update()
        if ASHP_cooling.X_eff < 0:
            ASHP_cooling_exergy_effi.append(0)
            ASHP_cooling_COP.append(0)
        else:          
            ASHP_cooling_exergy_effi.append(ASHP_cooling.X_eff)
            ASHP_cooling_COP.append(ASHP_cooling.COP)
    else:
        ASHP_cooling_exergy_effi.append(0)
        ASHP_cooling_COP.append(0)

    # 난방 엑서지 효율 계산
    if heating_load > 0:
        ASHP_heating = enex.AirSourceHeatPump_heating()
        ASHP_heating.T0 = Toa
        ASHP_heating.T_a_room = 22
        ASHP_heating.Q_r_int = heating_load
        ASHP_heating.Q_r_max = max(heating_load_list)
        ASHP_heating.system_update() 
        if ASHP_heating.X_eff < 0:
            ASHP_heating_exergy_effi.append(0)
            ASHP_heating_COP.append(0)
        else:
            ASHP_heating_exergy_effi.append(ASHP_heating.X_eff)
            ASHP_heating_COP.append(ASHP_heating.COP)
    else:
        ASHP_heating_exergy_effi.append(0)
        ASHP_heating_COP.append(0)


len(ASHP_cooling_COP), len(ASHP_heating_COP), len(ASHP_cooling_exergy_effi), len(ASHP_heating_exergy_effi)

(8760, 8760, 8760, 8760)

In [304]:
# 8760 시간의 엑서지 효율 그래프
fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(dm.cm2in(14), dm.cm2in(7)))
plt.subplots_adjust(left=0.1, right=0.95, top=0.9, bottom=0.15, wspace=0.1, hspace=0.1)

# Fontsize
label_fontsize = dm.fs(0.5)
tick_fontsize = dm.fs(-0.5)
legend_fontsize = dm.fs(-1.0)
subtitle_fontsize = dm.fs(-1.5)

# Common settings
label_pad = 4
line_width = 0.8

# Colors
ASHP_cooling_color = 'blue'
ASHP_heating_color = 'red'

ax.plot([eff * 100 for eff in ASHP_heating_exergy_effi], color=ASHP_heating_color, label='Heating exergy efficiency [%]', linewidth=line_width, alpha=0.5)
ax.plot([eff * 100 for eff in ASHP_cooling_exergy_effi], color=ASHP_cooling_color, label='Cooling exergy efficiency [%]', linewidth=line_width, alpha=0.5)
ax.set_xlabel('Hour of year [h]', fontsize=label_fontsize, labelpad=label_pad)
ax.set_ylabel('Exergy efficiency [%]', fontsize=label_fontsize, labelpad=label_pad)
ax.tick_params(axis='both', which='major', labelsize=tick_fontsize) 
ax.set_xticks(np.linspace(0, 8760, 7))
ax.set_ylim(0, 51)
ax.set_yticks(np.arange(0, 51, 10))
ax.grid(True, linestyle='--', alpha=0.6)
ax.legend(
    labels=['Heating exergy efficiency', 'Cooling exergy efficiency'],
    loc='upper right', ncol=2, frameon=False,
    fontsize=legend_fontsize, fancybox=False,
    columnspacing=1.00, labelspacing=0.8,
    bbox_to_anchor=(0.99, 0.995),
    handlelength=1.8
)

# Save and show the figure
plt.savefig('figure/exergy_efficiency.png', dpi=600)
dm.util.save_and_show(fig)

In [305]:
# 8760 시간의 COP 그래프
fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(dm.cm2in(14), dm.cm2in(7)))
plt.subplots_adjust(left=0.1, right=0.95, top=0.9, bottom=0.15, wspace=0.1, hspace=0.1)

# Fontsize
label_fontsize = dm.fs(0.5)
tick_fontsize = dm.fs(-0.5)
legend_fontsize = dm.fs(-1.0)
subtitle_fontsize = dm.fs(-1.5)

# Common settings
label_pad = 4
line_width = 0.8

# Colors
ASHP_cooling_color = 'blue'
ASHP_heating_color = 'red'

ax.plot([eff for eff in ASHP_heating_COP], color=ASHP_heating_color, label='Heating COP [ - ]', linewidth=line_width, alpha=0.5)
ax.plot([eff for eff in ASHP_cooling_COP], color=ASHP_cooling_color, label='Cooling COP [ - ]', linewidth=line_width, alpha=0.5)
ax.set_xlabel('Hour of year [h]', fontsize=label_fontsize, labelpad=label_pad)
ax.set_ylabel('COP [ - ]', fontsize=label_fontsize, labelpad=label_pad)
ax.tick_params(axis='both', which='major', labelsize=tick_fontsize) 
ax.set_xticks(np.linspace(0, 8760, 7))
ax.set_ylim(0, 6)
ax.set_yticks(np.arange(0, 7, 1))
ax.grid(True, linestyle='--', alpha=0.6)
ax.legend(
    labels=['Heating COP', 'Cooling COP'],
    loc='upper right', ncol=2, frameon=False,
    fontsize=legend_fontsize, fancybox=False,
    columnspacing=1.00, labelspacing=0.8,
    bbox_to_anchor=(0.99, 0.995),
    handlelength=1.8
)

# Save and show the figure
plt.savefig('figure/cop.png', dpi=600)
dm.util.save_and_show(fig)

In [358]:
months_to_plot = [1, 4, 8, 10, 12]
fig, axes = plt.subplots(len(months_to_plot), 2, figsize=(dm.cm2in(17), dm.cm2in(20)), sharex=False)
plt.subplots_adjust(left=0.05, right=0.95, top=0.97, bottom=0.05, hspace=0.35, wspace=0.25)

for i, month in enumerate(months_to_plot):
    month_df = weekday_df[weekday_df['Month'] == month]
    month_indices = month_df.index

    # 엑서지 효율 계산
    month_exergy_efficiency = []
    month_cop = []
    for _, row in month_df.iterrows():
        Toa = row['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)']
        Tia = row['CORE_ZN:Zone Air Temperature [C](TimeStep)']
        cooling_load = row['DistrictCooling:Facility [J](TimeStep)'] / 3600
        heating_load = row['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600

        exergy_effi = None
        cop = 0
        if cooling_load > 0:
            ASHP_cooling = enex.AirSourceHeatPump_cooling()
            ASHP_cooling.T0 = Toa
            ASHP_cooling.T_a_room = 22
            ASHP_cooling.Q_r_int = cooling_load
            ASHP_cooling.Q_r_max = max(cooling_load_list)
            ASHP_cooling.system_update()
            if 0 < ASHP_cooling.X_eff < 0.5:
                exergy_effi = ASHP_cooling.X_eff
                cop = ASHP_cooling.COP
            elif ASHP_cooling.X_eff >= 0.5:
                exergy_effi = 0.3
                cop = ASHP_cooling.COP
            else:
                exergy_effi = 0
                cop = 0
        elif heating_load > 0:
            ASHP_heating = enex.AirSourceHeatPump_heating()
            ASHP_heating.T0 = Toa
            ASHP_heating.T_a_room = 22
            ASHP_heating.Q_r_int = heating_load
            ASHP_heating.Q_r_max = max(heating_load_list)
            ASHP_heating.system_update()
            if 0 < ASHP_heating.X_eff < 0.5:
                exergy_effi = ASHP_heating.X_eff
                cop = ASHP_heating.COP
            elif ASHP_heating.X_eff >= 0.5:
                exergy_effi = 0.3
                cop = ASHP_heating.COP
            else:
                exergy_effi = 0
                cop = 0
        else:
            exergy_effi = 0
            cop = 0

        month_exergy_efficiency.append(exergy_effi * 100 if exergy_effi is not None else 0)
        month_cop.append(cop)

    # COP plot (왼쪽)
    axes[i, 0].plot(month_indices, month_cop, color='dm.gray7', linewidth=0.8)
    axes[i, 0].set_ylabel('COP [ - ]', fontsize=label_fontsize, labelpad=label_pad+2)
    axes[i, 0].set_title(f'COP Variation in Month {month}', fontsize=subtitle_fontsize)
    axes[i, 0].set_ylim(0, 6)
    axes[i, 0].grid(True, linestyle='--', alpha=0.5)

    # Exergy efficiency plot (오른쪽)
    axes[i, 1].plot(month_indices, month_exergy_efficiency, color='dm.red6', linewidth=0.8)
    axes[i, 1].set_ylabel('Exergy efficiency [%]', fontsize=label_fontsize, labelpad=label_pad+2)
    axes[i, 1].set_title(f'Exergy Efficiency Variation in Month {month}', fontsize=subtitle_fontsize)
    axes[i, 1].set_ylim(0, 40)
    axes[i, 1].grid(True, linestyle='--', alpha=0.5)

plt.savefig('figure/selected_months_cop_exergy_efficiency.png', dpi=600)
dm.util.save_and_show(fig)

In [145]:
# 1) 사용할 월과 부분집합 만들기
months_to_plot = [1, 4, 8, 10]

day_all = weekday_df['Date/Time_clean'].str.slice(3, 5).astype(int)  # 'MM/DD ...' → DD
mask = weekday_df['Month'].isin(months_to_plot) & day_all.between(15, 21)  # 21일까지로 수정
df_sub = weekday_df.loc[mask].copy()

# 표시/축용 보조 열
df_sub['Day'] = day_all[mask].values
hour_sub = df_sub['Date/Time_clean'].str.slice(6, 8).astype(int)  # '... HH:MM:SS' → HH
df_sub['xpos'] = df_sub['Day'] + hour_sub / 24.0  # 15.00 ~ 21.958...

# 최대 부하(정규화용) 한 번만 계산
Q_r_max_cooling = (df_sub['DistrictCooling:Facility [J](TimeStep)'] / 3600.0).max()
Q_r_max_heating = (df_sub['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0).max()

# 2) COP / 엑서지 계산 (부분집합에만 수행)
def compute_metrics(row):
    Toa = row['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)']
    cooling_load = row['DistrictCooling:Facility [J](TimeStep)'] / 3600.0
    heating_load = row['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0

    exergy_effi = 0.0
    cop = 0.0

    if cooling_load > 0:
        ASHP = enex.AirSourceHeatPump_cooling()
        ASHP.T0 = Toa
        ASHP.T_a_room = 22
        ASHP.Q_r_int = cooling_load
        ASHP.Q_r_max = Q_r_max_cooling
        ASHP.system_update()
        if ASHP.X_eff > 0:
            exergy_effi = ASHP.X_eff * 100.0
            cop = ASHP.COP_sys

    elif heating_load > 0:
        ASHP = enex.AirSourceHeatPump_heating()
        ASHP.T0 = Toa
        ASHP.T_a_room = 22
        ASHP.Q_r_int = heating_load
        ASHP.Q_r_max = Q_r_max_heating
        ASHP.system_update()
        if ASHP.X_eff > 0:
            exergy_effi = ASHP.X_eff * 100.0
            cop = ASHP.COP_sys

    return pd.Series({'COP': cop, 'ExergyEff': exergy_effi})

df_sub[['COP', 'ExergyEff']] = df_sub.apply(compute_metrics, axis=1)

# 3) 플롯 (부분집합만 순회)
fig, axes = plt.subplots(len(months_to_plot), 2,
                         figsize=(dm.cm2in(17), dm.cm2in(20)), sharex=False)
plt.subplots_adjust(left=0.08, right=0.92, top=0.97, bottom=0.05, hspace=0.35, wspace=0.4)

for i, month in enumerate(months_to_plot):
    mdf = df_sub[df_sub['Month'] == month].sort_values('xpos')

    # 왼쪽: 외기온도와 부하
    ax1 = axes[i, 0]
    ax2 = ax1.twinx()
    ax1.plot(mdf['xpos'], mdf['Environment:Site Outdoor Air Drybulb Temperature [C](TimeStep)'], 
             label='Toa [°C]', color='blue', linewidth=0.8)
    if month in [1, 10]:  # 난방 부하만
        ax2.plot(mdf['xpos'], mdf['DistrictHeatingWater:Facility [J](TimeStep) '] / 3600.0 / 1000, 
                 label='Heating Load [kW]', color='red', linewidth=0.8)
    elif month in [4, 8]:  # 냉방 부하만
        ax2.plot(mdf['xpos'], mdf['DistrictCooling:Facility [J](TimeStep)'] / 3600.0 / 1000, 
                 label='Cooling Load [kW]', color='orange', linewidth=0.8)

    ax1.set_ylabel('Environmental temperature [$\^{circ}$C]', fontsize=fs['label'], labelpad=pad['label'])
    ax2.set_ylabel('Load [kW]', fontsize=fs['label'], labelpad=pad['label'])
    ax1.set_title(f'{month}', fontsize=fs['subtitle'])
    ax1.grid(True, linestyle='--', alpha=0.5)
    ax1.legend(loc='upper left', fontsize=fs['legend'])
    ax2.legend(loc='upper right', fontsize=fs['legend'])
    ax1.set_ylim(-10, 35)  # 외기온도 y축 범위
    ax1.set_xlim(15, 22)  # x축 범위
    ax2.set_ylim(0, 30)    # 부하 y축 범위
    ax1.tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax2.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])

    # 오른쪽: COP와 엑서지 효율
    ax3 = axes[i, 1]
    ax4 = ax3.twinx()
    ax3.plot(mdf['xpos'], mdf['COP'], label='COP [ - ]', color='green', linewidth=0.8)
    ax4.plot(mdf['xpos'], mdf['ExergyEff'], label='Exergy Efficiency [%]', color='purple', linewidth=0.8)

    ax3.set_ylabel('Energy efficiency [ - ]', fontsize=fs['label'], labelpad=pad['label'])
    ax4.set_ylabel('Exergy efficiency [%]', fontsize=fs['label'], labelpad=pad['label'])
    ax3.set_title(f'{month}', fontsize=fs['subtitle'])
    ax3.grid(True, linestyle='--', alpha=0.5)
    ax3.legend(loc='upper left', fontsize=fs['legend'])
    ax4.legend(loc='upper right', fontsize=fs['legend'])
    ax3.set_ylim(0, 6)     # COP y축 범위
    ax4.set_ylim(0, 40)    # 엑서지 효율 y축 범위
    ax3.tick_params(axis='both', which='major', labelsize=fs['tick'], pad=pad['tick'])
    ax4.tick_params(axis='y', which='major', labelsize=fs['tick'], pad=pad['tick'])

dm.util.save_and_show(fig)
